In [7]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name =soup.find('h1', class_='FNkAEc o4k8l')
        hotel_name=name.text.strip()
        print("Name ",hotel_name)
        hotel_data['name'] = hotel_name
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            print("Address",add)
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    print(f"Image source: {img_src}")
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            print("Price:", price)
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='islamabad '
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            print("facilities 1",fac)
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            print("About", about)
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    print("About:", about1)
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    print("Facility:", fac)

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            print("rating average ",overall_rating)
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            print("rating average ",overallrating)
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            print("rating average ",overall)
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            print("total reviews ",total_rating)
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            print("total reviews ",total)
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            print("total reviews ",totalr)
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

                print("Username:", username_text)
                print("Rating:", rating_text)
                print("Review:", review_text)

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews

        # Append data to the DataFrame
        hotel_df = hotel_df.append(hotel_data, ignore_index=True)
        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        # Save the DataFrame to a CSV file
        csv_filename = 'hotel_data.csv'
        hotel_df.to_csv(csv_filename, index=False)
        print(f"Data saved to CSV file: {csv_filename}")

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'Fyp_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=islamabad&ts=CAESCgoCCAMKAggDEAAqBwoFOgNQS1I&ved=0CAAQ5JsGahcKEwion8vY3JmHAxUAAAAAHQAAAAAQag&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgmy2Y4KdMxAQBE113rA1DpSQBISCRbKIYRc30BAETXXeuCmSFJAMAA&qs=CAAgACgA')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[26]/div[1]/button/span')
        print("Found next page button.")
    except NoSuchElementException:
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[25]/div[1]/button[2]/span')
            print("Found alternate next page button.")
        except NoSuchElementException:
            # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'Fyp_db' does not exist. Creating database 'Fyp_db'.
Collection 'hotel_data' does not exist in database 'Fyp_db'. Creating collection 'hotel_data'.
Database 'Fyp_db' and collection 'hotel_data' are ready for use.


KeyboardInterrupt: 

In [ ]:
data_list.append({
            'Heading': heading_text,
            'Brand': brand_text,
            'Color': color_text,
            'Description': description_text,
            'Price': price_text,
            'Review': reviews_text,
            'gender': gender_text, 
            'category': category,
            'URL': article_url,
            'Image_Src': image_src_list  # Store image sources in the DataFrame
        })


In [10]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name =soup.find('h1', class_='FNkAEc o4k8l')
        hotel_name=name.text.strip()
        print("Name ",hotel_name)
        hotel_data['name'] = hotel_name
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            print("Address",add)
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    print(f"Image source: {img_src}")
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            print("Price:", price)
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Kashmir '
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            print("facilities 1",fac)
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            print("About", about)
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    print("About:", about1)
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    print("Facility:", fac)

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            print("rating average ",overall_rating)
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            print("rating average ",overallrating)
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            print("rating average ",overall)
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            print("total reviews ",total_rating)
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            print("total reviews ",total)
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            print("total reviews ",totalr)
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

                print("Username:", username_text)
                print("Rating:", rating_text)
                print("Review:", review_text)

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        # Save the DataFrame to a CSV file
        csv_filename = 'hotel_data.csv'
        hotel_df.to_csv(csv_filename, index=False)
        print(f"Data saved to CSV file: {csv_filename}")

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=kashmir%20hotels&ts=CAESCgoCCAMKAggDEAAqBwoFOgNQS1I&ved=0CAAQ5JsGahgKEwio0bHM-q6HAxUAAAAAHQAAAAAQ7QI&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgn741klkr9AQBGtdHd9OzRSQBISCXBZ1RZm5UBAEa10d73fT1JAMAA&qs=CAAgACgA')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[23]/div[1]/button/span')
        print("Found next page button.")
    except NoSuchElementException:
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[25]/div[1]/button[2]/span')
            print("Found alternate next page button.")
        except NoSuchElementException:
            # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'new_db' does not exist. Creating database 'new_db'.
Collection 'hotel_data' does not exist in database 'new_db'. Creating collection 'hotel_data'.
Database 'new_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 18 links from page 1.
Found next page button.
Scraping page 2...
Collected 20 links from page 2.
Found alternate next page button.
Scraping page 3...
Collected 7 links from page 3.
No more pages found. Stopping the scraping process.
All Scraped data from links:
1
Name  Hotel Star of Kashmir
Address •
Image source: https://lh5.googleusercontent.com/p/AF1QipM2I3_DCDuL-kOwZ4eRZL9TcUUA7qaCxqNeV3ch=w252-h252-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipM2I3_DCDuL-kOwZ4eRZL9TcUUA7qaCxqNeV3ch=w252-h252-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipO1EG8kieHKp5UpctK_kYsDkkwlprXvIc3-NY3U=w252-h189-k-no
Price: Rs 9,002
About: Set in a residential area, this unpretentious hotel is 5 km from Ghanta Ghar Clock Tower, 8 km

Name  Hotel Kashmir Inn
Address •
Image source: https://lh5.googleusercontent.com/p/AF1QipNURkzSpvRVvcA6VKjTS2elpz6JutW8r0ck1Mw=w252-h189-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipNTPMv8Warc4gy1F52HenJYCBZu_RyLxL0l1Nw=w252-h142-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipMXcOpMnSAHUJ-RqyO8ch1oH5SID_t10PHOF9o=w252-h167-k-no
Price: Rs 3,353
About: Check-in time: 11:00Check-out time: 11:00
Facility: PoolWi-FifreeParkingextra chargeAirport shuttle
Facility: InternetWi-FifreeWi-Fi in public areasPublic Internet workstationServicesFront desk24-hourBaggage storageCurrency exchangeFull-service laundrySocial hourHousekeepingdailyPoolsPoolNo hot tubParking & transportParkingextra chargeAirport shuttleextra chargePrivate car serviceextra chargeCar rental onsiteLocal shuttleLanguages spokenEnglishHindiFood and drinkNo breakfastPolicies & paymentsSmoke-free propertyCredit cardsDebit cardsNFC mobile paymentsCashChequesChildrenChild-friendlyBabysittingActivities fo

Name  Hotel Kashmir Hilltown
Address •
Image source: //lh4.googleusercontent.com/proxy/nV9zQTdQotRdEDQUDm-JPZsjgjUTpmKDS4LrmBNIHstURTe893G1og4Bp_nsuTK9cyVPNBthOSfySMpSREaGA63jFB-hLi0KAk75RaIzL0FaeaDSZzH8YNB8KznbAx2Ghxy6CE1uDMVy7TwLzphQjUh4HRnt5gw=w252-h185-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipPoYrxnGou2ytDvwyMZVbLPVDCrwa4Pd3XQgpIO=w252-h189-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipPQ8-2r5bndOvd9q35AHT-JiCS004pSsUrW1-n8=w252-h448-k-no
Price: Rs 9,003
About: Check-in time: 14:00
Facility: PoolWi-FifreeParking
Facility: InternetWi-FifreeChildrenChild-friendlyParking & transportParkingLocal shuttleRoomsKitchenServicesFront desk24-hourFull-service laundryPoolsPoolNo hot tubWellnessNo fitness centreNo spa
rating average  3.6
total reviews  151 reviews
Username: Savita Jadhav
Rating: 1/5
Review: Very very bad experience with this hotel.It’s a genuine suggestion to those who are looking for this hotel, don’t book this hotel even if they give free of 

Name  Kashmir Holiday Resort
Address By Dal Lake, Foreshore Rd, Habak, Nagin Bagh, Srinagar, Jammu and Kashmir 190006
Image source: //lh6.googleusercontent.com/proxy/WtOKcQ-R3lI08fXL4wBDXUJqnMAjqQPiZPV0Tjl0fNchN80ZixurqSg1oNs84XEgMP9PPBHWr32BYXJqOBOQT9VLUqqMNem72en6OT5os2DuCxdqf_ysbVu2KTIJQe5Jefq4TiTIdsPE0oOlg1Zrq_IehCRSBCY=w252-h168-k-no
Image source: //lh5.googleusercontent.com/proxy/5QVBAjOBQhBajtPVe8TNe0gqHRSgzTWSxI8llW3yU4U6r9zhzzGyG6A4KXEu7dm2heIK3RaLQeE9kn5oOm6qSuca9aSxuFk_QBp1bdLk5FgEU_Y5d7wTIUGbxj62twr-NPqxvabrMlFyYxD9bGZpYGE2hsLOxQ=w252-h194-k-no
Image source: //lh5.googleusercontent.com/proxy/Iby_t_WIjsEy8QESgcyERDw0E2QxjyTLAJSbd4Sq4pA5wE9S5ikSCmFU8C2QEPQWxm96LGrD4yddvlUP4Z47Jn_madPsVBmy3b6GovQOEGLs0nXrsb878Kd-5XKMTykdzw1_aG2wmdguAj1dt70m8737oOa2MR0=w252-h168-k-no
Price: Rs 15,366
About: Check-in time: 15:00Check-out time: 11:00
Facility: ParkingfreeWi-FifreeAir conditioningBreakfast
Facility: InternetWi-FifreePolicies & paymentsSmoke-free propertyCredit cardsDebit cardsNFC 

Price: Rs 3,475
About: Check-in time: 12:00Check-out time: 12:00
Facility: ParkingfreeBreakfastfreeWi-FifreeAir conditioning
Facility: InternetWi-FifreeWi-Fi in public areasServicesFront desk24-hourFull-service laundryParking & transportParkingfreeSelf parkingfreeAirport shuttleextra chargeLocal shuttleRoomsAir conditioning in some roomsFood and drinkRoom serviceBreakfastfreePoolsNo poolsNo hot tubWellnessNo fitness centreNo spaPetsNo petsBathroomsPrivate bathroomShower
rating average  4.0
total reviews  112 reviews
Username: Aftab Qureshi
Rating: 3/5
Review: Kaml service lajwab log very niceRooms5.0Service5.0Location5.0
Username: Farhan A
Rating: 1/5
Review: I just got opertunity to stay there with  3 friends, It is one the best low budget hotel for families and friends.The service and staff was outstanding, and super cooperative.We were welcomed by a beautiful gentleman probably the owner or Manger, he was such a nice person with positive vibe (growing beard). Despite the fact that i

...

Name  Hotel Heevan & Restaurant
Address Old, Zero Bridge, Rajbagh, Srinagar, Jammu and Kashmir 190001
Image source: https://lh5.googleusercontent.com/p/AF1QipNQ63W7PTsZMmZ53gFG0Rc8xQQqgZ-tOpBgvxA=w252-h189-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipMZHGmLNq7q-lctKp1rvYibrRZa-B0n63unifxM=w252-h448-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipNQ63W7PTsZMmZ53gFG0Rc8xQQqgZ-tOpBgvxA=w252-h189-k-no
Price element not found.
About: Check-in time: 14:00Check-out time: 12:00
rating average  4.1
total reviews  16 reviews
Username: Monika G
Rating: 5/5
Review: This place here in pehale aam ..we enjoyed the ambience food & service of the hotel staff especially Mr. Hilal supervisor of house keeping .. He helped us to take our friend to the Doctor .. we appreciate his help . We highly recommend people to visit & enjoy this property.
Username: Chandan P
Rating: 4/5
Review: 😌Rooms5.0Service1.0Location4.0Hotel highlightsRomantic
Username: sonal5871
Rating: 5/5
Review: N

Name  Hotel Kashmir Palace
Address Chandanwari Rd, near First Bridge, Laripora, Pahalgam, Jammu and Kashmir 192126
Image source: https://lh5.googleusercontent.com/p/AF1QipPlryntb0_FhOYLYzZfVdBGrDR-SdhR2amv_52k=w252-h188-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipPlryntb0_FhOYLYzZfVdBGrDR-SdhR2amv_52k=w252-h188-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipPbwI936ex8BT1t8RfOZIYteDLvCPoz2wPPSj0Q=w252-h188-k-no
Price element not found.
About: Check-in time: 14:00Check-out time: 11:00
rating average  3.9
total reviews  7 reviews
Username: Nitin Comar
Rating: 4/5
Review: I stumbled across this place when I had to goto Pahalgam at short notice and nothing was available. They had one room so, I stayed here. Very basic room and accommodation but clean. I was surprised by the food they served.. the best chicken curry. They have access to the river and the staff is very helpful and will make sure your stay is comfortable. Great value for money.Rooms2.0Service4.0L

Name  OYO 811854 Misty Resorts & Spa
Address Mufti Bagh-Harwan Rd, Srinagar, Jammu and Kashmir 191202
Image source: https://lh5.googleusercontent.com/p/AF1QipOrFC2_MLFQdK2wg6hSugshySj-HPZH_OQvGv0w=w252-h189-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipNpy83agAAHkpFeNt7mzzKvrXqz5NHB0UnJCbAJ=w252-h168-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipPp-ZVzHkYv0bcA1BaSTD3vW_NyDW_hoiD_bHGE=w252-h189-k-no
Price element not found.
About section not found.
rating average  5.0
total reviews  1 review
Username: Misty Infra Holdings
Rating: 5/5
Review: Incredible location and stayRooms5.0Service5.0Location5.0
Data saved to CSV file: hotel_data.csv
Inserted data for hotel: OYO 811854 Misty Resorts & Spa
Stored data for hotel: OYO 811854 Misty Resorts & Spa
Address: Mufti Bagh-Harwan Rd, Srinagar, Jammu and Kashmir 191202
Price: N/A
Total Reviews: 1 review
Average Review: 5.0
About: N/A
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipOrFC2_MLFQdK2wg6hSugs

Name  Hotel Naya Kashmir
Address 3RC6+C52, U&I, Lal Chowk, Srinagar, Jammu and Kashmir 190001
Image source: https://lh5.googleusercontent.com/p/AF1QipOQLgSlfAOEiISrNcJ9_wlxoGBGt-I340VIzOxv=w252-h335-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipOQLgSlfAOEiISrNcJ9_wlxoGBGt-I340VIzOxv=w252-h335-k-no
Image source: https://lh5.googleusercontent.com/p/AF1QipMCxcnbEDScHGvSWbdU0IYdinrUXzVaMQYLvcO3=w252-h336-k-no
Price element not found.
About: Check-in time: 14:00Check-out time: 12:00
rating average  CloseView list
total reviews  3.7 (63)Free Wi-Fi0.1 km away
Data saved to CSV file: hotel_data.csv
Inserted data for hotel: Hotel Naya Kashmir
Stored data for hotel: Hotel Naya Kashmir
Address: 3RC6+C52, U&I, Lal Chowk, Srinagar, Jammu and Kashmir 190001
Price: N/A
Total Reviews: 3.7 (63)Free Wi-Fi0.1 km away
Average Review: CloseView list
About: Check-in time: 14:00Check-out time: 12:00
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipOQLgSlfAOEiISrNcJ9_wlxoGBGt-I340

Name  kashmir khalsa hotel
Address Amira Kadal Bridge, near gurduwara, Lal Chowk, Srinagar, Jammu and Kashmir 190001
Image source: https://lh5.googleusercontent.com/p/AF1QipNIgyldzl07b0m59i5xp0wvJOpTtL6C39ZLtZXK=w252-h449-k-no?w=1024
Price element not found.
About section not found.
rating average  CloseView list
total reviews  4.6 (465)Free breakfast and Wi-Fi0.6 km away
Username: Abhishek C
Rating: 5/5
Review: Kashmir khalsa hotel is a very nice and awesome hotel. It is a budjet hotel but it has many facalities like room has tv, cleab bathroom. All staffs are friendly and it was our very choice hotel. I will definitely stay in this hotel whenever I will come here.
Username: sushil k
Rating: 5/5
Review: The hotel is very close to the city and easily accessible. It is an excellent hotel and this hotel is run by the most excellent people. Room service was nice and there were no any delay in the room service.
Data saved to CSV file: hotel_data.csv
Inserted data for hotel: kashmir khalsa 

In [72]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name = soup.find('h1', class_='FNkAEc o4k8l')
        if name:
            hotel_name = name.text.strip()
            print("Name:", hotel_name)
            hotel_data['name'] = hotel_name
        else:
            print("Hotel name not found.")
            hotel_data['name'] = None 
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            print("Address",add)
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    print(f"Image source: {img_src}")
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            print("Price:", price)
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Lahore'
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            print("facilities 1",fac)
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            print("About", about)
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    print("About:", about1)
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    print("Facility:", fac)

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            print("rating average ",overall_rating)
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            print("rating average ",overallrating)
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            print("rating average ",overall)
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            print("total reviews ",total_rating)
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            print("total reviews ",total)
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            print("total reviews ",totalr)
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

                print("Username:", username_text)
                print("Rating:", rating_text)
                print("Review:", review_text)

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        # Save the DataFrame to a CSV file
        csv_filename = 'hotel_data.csv'
        hotel_df.to_csv(csv_filename, index=False)
        print(f"Data saved to CSV file: {csv_filename}")

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=lahore%20hotel&ts=CAESCgoCCAMKAggDEAAqBwoFOgNQS1I&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEglNhFKeq7xAQBHkiweFJzVSQBISCXe4AhuC4kBAEeSLB8XLUFJAMAA&qs=CAAgACgA&ved=0CAAQ5JsGahgKEwi43pjEk7GHAxUAAAAAHQAAAAAQ7wI')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1
max_hotels = 450

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    if len(all_links) >= max_hotels:
        all_links = all_links[:max_hotels]  # Limit the total links to max_hotels
        break
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '/html/body/c-wiz[2]/div/c-wiz/div[1]/div[1]/div[2]/div[2]/main/c-wiz/span/c-wiz/c-wiz[26]/div[1]/button/span')
        print("Found next page button.")
    except NoSuchElementException:
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '/html/body/c-wiz[2]/div/c-wiz/div[1]/div[1]/div[2]/div[2]/main/c-wiz/span/c-wiz/c-wiz[26]/div[1]/button[2]/span')
            print("Found alternate next page button.")
        except NoSuchElementException:
            # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'new_db' exists.
Collection 'hotel_data' exists in database 'new_db'.
Database 'new_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 18 links from page 1.
No more pages found. Stopping the scraping process.
All Scraped data from links:
1


NoSuchWindowException: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=126.0.6478.127)
Stacktrace:
	GetHandleVerifier [0x00007FF769F1EEA2+31554]
	(No symbol) [0x00007FF769E97ED9]
	(No symbol) [0x00007FF769D5872A]
	(No symbol) [0x00007FF769D2D995]
	(No symbol) [0x00007FF769DD44D7]
	(No symbol) [0x00007FF769DEC051]
	(No symbol) [0x00007FF769DCCDD3]
	(No symbol) [0x00007FF769D9A33B]
	(No symbol) [0x00007FF769D9AED1]
	GetHandleVerifier [0x00007FF76A228B1D+3217341]
	GetHandleVerifier [0x00007FF76A275AE3+3532675]
	GetHandleVerifier [0x00007FF76A26B0E0+3489152]
	GetHandleVerifier [0x00007FF769FCE776+750614]
	(No symbol) [0x00007FF769EA375F]
	(No symbol) [0x00007FF769E9EB14]
	(No symbol) [0x00007FF769E9ECA2]
	(No symbol) [0x00007FF769E8E16F]
	BaseThreadInitThunk [0x00007FF80D3B257D+29]
	RtlUserThreadStart [0x00007FF80E6AAF28+40]


In [ ]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name = soup.find('h1', class_='FNkAEc o4k8l')
        if name:
            hotel_name = name.text.strip()
            print("Name:", hotel_name)
            hotel_data['name'] = hotel_name
        else:
            print("Hotel name not found.")
            hotel_data['name'] = None 
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            print("Address",add)
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    print(f"Image source: {img_src}")
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            print("Price:", price)
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Lahore'
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            print("facilities 1",fac)
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            print("About", about)
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    print("About:", about1)
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    print("Facility:", fac)

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            print("rating average ",overall_rating)
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            print("rating average ",overallrating)
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            print("rating average ",overall)
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            print("total reviews ",total_rating)
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            print("total reviews ",total)
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            print("total reviews ",totalr)
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

                print("Username:", username_text)
                print("Rating:", rating_text)
                print("Review:", review_text)

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        # Save the DataFrame to a CSV file
        csv_filename = 'hotel_data.csv'
        hotel_df.to_csv(csv_filename, index=False)
        print(f"Data saved to CSV file: {csv_filename}")

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=lahore%20hotel&ts=CAESCgoCCAMKAggDEAAqBwoFOgNQS1I&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEglNhFKeq7xAQBHkiweFJzVSQBISCXe4AhuC4kBAEeSLB8XLUFJAMAA&qs=CAAgACgA&ved=0CAAQ5JsGahgKEwi43pjEk7GHAxUAAAAAHQAAAAAQ7wI')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1
max_hotels = 450

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    if len(all_links) >= max_hotels:
        all_links = all_links[:max_hotels]  # Limit the total links to max_hotels
        break
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '/html/body/c-wiz[2]/div/c-wiz/div[1]/div[1]/div[2]/div[2]/main/c-wiz/span/c-wiz/c-wiz[26]/div[1]/button/span')
        print("Found next page button.")
    except NoSuchElementException:
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '/html/body/c-wiz[2]/div/c-wiz/div[1]/div[1]/div[2]/div[2]/main/c-wiz/span/c-wiz/c-wiz[26]/div[1]/button[2]/span')
            print("Found alternate next page button.")
        except NoSuchElementException:
            # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


In [15]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'fyp_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")

# Initialize the browser
browser = webdriver.Chrome()
browser.get('https://www.google.com/travel/search?q=islamabad&ts=CAESCgoCCAMKAggDEAAqBwoFOgNQS1I&ved=0CAAQ5JsGahcKEwion8vY3JmHAxUAAAAAHQAAAAAQag&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgmy2Y4KdMxAQBE113rA1DpSQBISCRbKIYRc30BAETXXeuCmSFJAMAA&qs=CAAgACgA')
browser.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(browser.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")
    browser.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = browser.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[26]/div[1]/button/span')
        print("Found next page button.")
    except NoSuchElementException:
        try:
            # Try the alternate next page button
            next_button = browser.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[25]/div[1]/button[2]/span')
            print("Found alternate next page button.")
        except NoSuchElementException:
            # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

# Close the browser after collecting all the main links
browser.quit()

# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about', 'facilities', 'images', 'reviews'
])

# Now, iterate over each collected link to extract detailed information
for link in all_links:
    print(f"Processing link: {link}")
    browser = webdriver.Chrome()
    browser.get(link)
    sleep(5)
    
    hotel_data = {}
    try:
        # Wait for the hotel name to be visible and extract it
        hotel_name = WebDriverWait(browser, 10).until(
            EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
        ).text
        hotel_data['name'] = hotel_name
        
        # Extract other details similarly
        hotel_data['address'] = browser.find_element(By.XPATH, '//span[@class="LrzXr"]').text
        hotel_data['price'] = browser.find_element(By.XPATH, '//span[@class="e10twf7w0"]').text
        hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

        # Extract facilities - assuming they are within a specific container
        facilities = browser.find_elements(By.XPATH, '//div[@class="xyT94e"]')
        hotel_data['facilities'] = [facility.text for facility in facilities]

        # Extract images
        images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        hotel_data['images'] = [img.get_attribute('src') for img in images[:3]]  # Get up to 3 images

        # Extract reviews - assuming a container or a way to load more reviews
        reviews_elements = browser.find_elements(By.XPATH, '//div[@class="YibKl"]')
        reviews = []
        for review in reviews_elements:
            try:
                user_name = review.find_element(By.XPATH, './/div[@class="d4r55"]').text
                user_rating = review.find_element(By.XPATH, './/div[@class="Fam1ne EBe2gf"]').get_attribute('aria-label')
                user_review = review.find_element(By.XPATH, './/span[@class="review-full-text"]').text
                reviews.append({
                    'user_name': user_name,
                    'user_rating': user_rating,
                    'user_review': user_review
                })
            except NoSuchElementException:
                continue
        hotel_data['reviews'] = reviews

        # Append data to the DataFrame
        hotel_df = hotel_df.append(hotel_data, ignore_index=True)

        print(f"Stored data for hotel: {hotel_name}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")
    
    finally:
        browser.quit()

print("Scraping complete.")

# Remove duplicates based on 'name' column
hotel_df.drop_duplicates(subset=['name'], inplace=True)

# Save the DataFrame to a CSV file
csv_filename = 'hotel_data.csv'
hotel_df.to_csv(csv_filename, index=False)
print(f"Data saved to CSV file: {csv_filename}")

# Insert non-duplicate data into MongoDB
for index, row in hotel_df.iterrows():
    hotel_name = row['name']
    # Check if the hotel already exists in the collection
    if collection.find_one({'name': hotel_name}) is None:
        collection.insert_one(row.to_dict())
        print(f"Inserted data for hotel: {hotel_name}")
    else:
        print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")

print("Data storage in MongoDB complete.")


Database 'fyp_db' exists.
Collection 'hotel_data' exists in database 'fyp_db'.
Database 'fyp_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 20 links from page 1.
Found next page button.
Scraping page 2...
Collected 20 links from page 2.
Found alternate next page button.
Scraping page 3...
Collected 20 links from page 3.


NoSuchWindowException: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=126.0.6478.127)
Stacktrace:
	GetHandleVerifier [0x00007FF769F1EEA2+31554]
	(No symbol) [0x00007FF769E97ED9]
	(No symbol) [0x00007FF769D5872A]
	(No symbol) [0x00007FF769D2D995]
	(No symbol) [0x00007FF769DD44D7]
	(No symbol) [0x00007FF769DEC051]
	(No symbol) [0x00007FF769DCCDD3]
	(No symbol) [0x00007FF769D9A33B]
	(No symbol) [0x00007FF769D9AED1]
	GetHandleVerifier [0x00007FF76A228B1D+3217341]
	GetHandleVerifier [0x00007FF76A275AE3+3532675]
	GetHandleVerifier [0x00007FF76A26B0E0+3489152]
	GetHandleVerifier [0x00007FF769FCE776+750614]
	(No symbol) [0x00007FF769EA375F]
	(No symbol) [0x00007FF769E9EB14]
	(No symbol) [0x00007FF769E9ECA2]
	(No symbol) [0x00007FF769E8E16F]
	BaseThreadInitThunk [0x00007FF80D3B257D+29]
	RtlUserThreadStart [0x00007FF80E6AAF28+40]


In [2]:
import pandas as pd

# File name of the CSV
csv_filename = 'hotel_data.csv'

# Read the data from the CSV file
hotel_df = pd.read_csv(csv_filename)

# Display the first few rows of the DataFrame to verify
print(hotel_df)

# Check the data types and information about the DataFrame
print(hotel_df.info())


                   name     address     price  \
0  Island - Double Room  no address  Rs 6,710   

                             total_reviews  average_review  \
0  Rs 6,710 total1 night with taxes + fees  CloseView list   

                                               about      city  \
0  DetailsAttractively situated in the Dal Lake d...  Kashmir    

                                          facilities  \
0  ['Entire house', 'Sleeps 2', '1 bedroom', '1 b...   

                                              images  \
0  ['https://lh6.googleusercontent.com/proxy/KjKQ...   

                                             reviews  
0  [{'username': 'Anand', 'rating': '10/10', 'rev...  
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1 entries, 0 to 0
Data columns (total 10 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   name            1 non-null      object
 1   address         1 non-null      object
 2   price           1 non-nul

In [96]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name = soup.find('h1', class_='FNkAEc o4k8l')
        if name:
            hotel_name = name.text.strip()
            
            hotel_data['name'] = hotel_name
        else:
            print("Hotel name not found.")
            hotel_data['name'] = None 
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Lahore'
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    
                    hotel_data['about'] = about1
                else:
                    
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            hotel_data['total_reviews'] = totalr
        else: 
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

                

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        # Save the DataFrame to a CSV file
        csv_filename = 'hotel_data.csv'
        hotel_df.to_csv(csv_filename, index=False)
        print(f"Data saved to CSV file: {csv_filename}")

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=lahore%20hotel&ts=CAESCgoCCAMKAggDEAAaTwoxEi8yJTB4MzkxOTA0ODNlNTgxMDdkOToweGMyM2FiZTZjY2M3ZTI0NjI6BkxhaG9yZRIaEhQKBwjoDxAIGAESBwjoDxAIGAIYATICEAAqBwoFOgNQS1I&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEglNhFKeq7xAQBHkiweFJzVSQBISCXe4AhuC4kBAEeSLB8XLUFJAMAG6AQdyZXZpZXdz&qs=CAESBENEWT0gACgAOA1IAA&ved=0CAAQ5JsGahgKEwiYndraprGHAxUAAAAAHQAAAAAQzwI')
driver.maximize_window()

# Allow some time for the page to load
sleep(3)

all_links = []
page_number = 1
max_hotels = 450

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    if len(all_links) >= max_hotels:
        all_links = all_links[:max_hotels]  # Limit the total links to max_hotels
        break
        
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[23]/div[1]/button/span')
        print("Found next page button.")
    except NoSuchElementException:
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[25]/div[1]/button[2]/span')
            print("Found alternate next page button.")
        except NoSuchElementException:
            # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'new_db' exists.
Collection 'hotel_data' exists in database 'new_db'.
Database 'new_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 20 links from page 1.
Found alternate next page button.
Scraping page 2...
Collected 20 links from page 2.
Found alternate next page button.
Scraping page 3...
Collected 20 links from page 3.
Found alternate next page button.
Scraping page 4...
Collected 20 links from page 4.
Found alternate next page button.
Scraping page 5...
Collected 20 links from page 5.
Found alternate next page button.
Scraping page 6...
Collected 20 links from page 6.
Found alternate next page button.
Scraping page 7...
Collected 20 links from page 7.
Found alternate next page button.
Scraping page 8...
Collected 20 links from page 8.
Found alternate next page button.
Scraping page 9...
Collected 20 links from page 9.
Found alternate next page button.
Scraping page 10...
Collected 20 links from page 10.
Found alternate next page button.
Scra

Data saved to CSV file: hotel_data.csv
Inserted data for hotel: Carlton Tower Hotel Lahore
Stored data for hotel: Carlton Tower Hotel Lahore
Address: •
Price: Rs 10,440
Total Reviews: 393 reviews
Average Review: 3.9
About: In a residential area, this unassuming hotel is a kilometer from Lahore Junction train station, 4 km from the 17th-century Badshahi Mosque and 17 km from Allama Iqbal International Airport.… MoreThe casual rooms come with complimentary Wi-Fi, flat-screen TVs, and tea and coffeemaking facilities. Room service is available.Complimentary valet parking is available. Amenities include a simple restaurant, a bar and BBQ facilities.Check-in time: 07:00Check-out time: 12:00
Facilities: ParkingfreeAir conditioningBreakfastfreeWi-Fi, InternetWi-FiServicesFront desk24-hourFull-service laundryPoolsNo poolsWellnessNo fitness centreNo spaRoomsAir conditioningFood and drinkRestaurantRoom serviceBreakfastfreeChildrenChild-friendlyParking & transportParkingfreeAirport shuttleextra ch

Data saved to CSV file: hotel_data.csv
Inserted data for hotel: Lotus One Hotel
Stored data for hotel: Lotus One Hotel
Address: •
Price: Rs 6,326
Total Reviews: 888 reviews
Average Review: 4.0
About: In a commercial area 8 minutes' walk from the closest bus stop, this straightforward hotel is 8 km from the mini zoo at Gulshan-e-Iqbal Park and 10 km from the Shakir Ali Museum.… MoreThe warm, relaxed rooms offer free Wi-Fi, flat-screen TVs and minifridges, plus en suite wet rooms. Some upgraded rooms sleep up to 4 guests and/or have sitting areas. Room service is available 24/7.There's a casual eatery. Other amenities include 24-hour security, meeting space and a simple lobby TV lounge. A backup generator is on-site.Check-in time: 13:00Check-out time: 12:00
Facilities: ParkingfreeAir conditioningBreakfastfreeWi-Fifree, InternetWi-FifreeServicesFront desk24-hourFull-service laundryPoolsNo poolsNo hot tubWellnessNo fitness centreNo spaBusiness & eventsMeeting roomsRoomsAir conditioningFood

Data saved to CSV file: hotel_data.csv
Inserted data for hotel: Hotel Royal Rose
Stored data for hotel: Hotel Royal Rose
Address: 531, opposite Jinnah Hospital, Block A Faisal Town, Lahore, Punjab 54700
Price: Rs 3,248
Total Reviews: 31 reviews
Average Review: 4.5
About: Check-in time: 12:00Check-out time: 11:30
Facilities: ParkingfreeAir conditioningWi-FifreeBreakfastextra charge, InternetWi-FifreeWi-Fi in public areasPolicies & paymentsSmoke-free propertyNo credit cardsNFC mobile paymentsCashChildrenChild-friendlyPoolsNo poolsNo hot tubWellnessNo fitness centreNo spaDoctor on callAccessibilityNot accessibleAccessible parkingRoomsAir conditioningKitchen in some roomsRefrigerator in some roomsMicrowave in some roomsFood and drinkRoom serviceBreakfastextra chargeServicesFront desk24-hourBaggage storageConciergeGrocery shopCurrency exchangeFull-service laundryWake up callsHousekeepingdailyParking & transportParkingfreeSelf parkingfreeAirport shuttleextra chargePrivate car serviceextra ch

Data saved to CSV file: hotel_data.csv
Inserted data for hotel: MaryLeena Hotel Gulberg
Stored data for hotel: MaryLeena Hotel Gulberg
Address: 17, Block P Gulberg 2, Lahore, Punjab 54660
Price: Rs 6,771
Total Reviews: 342 reviews
Average Review: 4.0
About: Among commercial and residential properties, this casual hotel is a 15-minute walk from Block T Park, 2 km from Lahore Cantt. Railway Station and 3 km from Gaddafi Stadium.… MoreThe warmly furnished rooms provide Wi-Fi, flat-screen TVs, safes and minibars. All feature soundproof windows and sitting areas. Upgraded rooms add whirlpool baths. Room service is available.Amenities include parking and continental breakfast.Check-in time: 10:30Check-out time: 12:00
Facilities: ParkingfreeAir conditioningBreakfastfreeWi-Fi, InternetWi-FiServicesFront desk24-hourFull-service laundryParking & transportParkingfreeAirport shuttleextra chargePetsNo petsFood and drinkRoom serviceBreakfastfreePoolsNo poolsNo hot tubWellnessNo fitness centreNo spaR

...

Price element not found.
Data saved to CSV file: hotel_data.csv
Inserted data for hotel: Grace Inn Hotel
Stored data for hotel: Grace Inn Hotel
Address: 16-C, Main Raiwind Rd, Phase 1 Judicial Colony, Lahore, Punjab 54782
Price: N/A
Total Reviews: 35 reviews
Average Review: 3.6
About: Check-out time: 12:00
Facilities: ParkingfreeWi-Fifree, InternetWi-FifreeServicesFront desk24-hourFull-service laundryParking & transportParkingfreeFood and drinkRoom servicePoolsNo poolsNo hot tubWellnessNo fitness centreNo spa
Images: https://lh5.googleusercontent.com/p/AF1QipO5GTjzPLuDQsQDcLMkhC4nNBoNxRPEcIuYYL_4=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipO5GTjzPLuDQsQDcLMkhC4nNBoNxRPEcIuYYL_4=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipOVdVHIi6LFfU3495_3h-XoFksS3qAuC5RWkf76=w252-h189-k-no
Reviews:
  Username: Tariq Hayat
  Rating: 1/5
  Review: Worst place, greedy staff no room service, never visit with family. It's horrible
  Username: Muhammad kamran zafar
  Rating: 3/5


address not avalible
Data saved to CSV file: hotel_data.csv
Inserted data for hotel: One Bedroom Apartment Penta Square Phase 5 DHA Lahore
Stored data for hotel: One Bedroom Apartment Penta Square Phase 5 DHA Lahore
Address: no address
Price: Rs 21,703
Total Reviews: Rs 21,703 total1 night with taxes + fees
Average Review: CloseView list
About: DetailsThis apartment is located in Lahore. Chughtai Museum and Faqir Khana Museum are cultural highlights, and some of the area's attractions include Joyland and Lahore Zoo. X Park and Sozo Water Park are also worth visiting.   From our spacious balcony you can enjoy a unique view of Penta Square's vicinity and the magic fountains•Centralized Cooling and Heating System•New and modern building• Fully-equipped kitchen, including stainless steel appliances• Comfortable bed, air conditioning and black out curtains• Free parking available in the buildingFeatures:24/7 backup Power GenerationAutomated Parking Entrance  Exit2-Minute Drive from Lahore R

Price element not found.
Data saved to CSV file: hotel_data.csv
Inserted data for hotel: Asaish Inn Guest House Lahore
Stored data for hotel: Asaish Inn Guest House Lahore
Address: House No. 23, Main Shan Bhatti Rd, Block K Phase 2 Ali Town, Lahore, Punjab 87340
Price: N/A
Total Reviews: 23 reviews
Average Review: 4.2
About: N/A
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipM_O6_GBdv9ymznpxT-DDk_7yWGUwDs6TFXlI1s=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipO3uvWMh5Ur71zW7DiO3QjN-diHcJjqGqrx9Sd7=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipOWdjkAAGTVi0Vfd4g-v_AP_OK-wehbkFzUCAtU=w252-h189-k-no
Reviews:
  Username: SALEEM AKRAM
  Rating: 5/5
  Review: I recently stayed at guest house that exceeded my expectations in every way. The location was superb, providing easy access to the city center, making exploration and commuting hassle-free. The staff was incredibly accommodating and friendly, offering impeccable service throughout my stay. The rooms

Price element not found.
Data saved to CSV file: hotel_data.csv
Inserted data for hotel: Windmills Hotel
Stored data for hotel: Windmills Hotel
Address: G953+33X, Riaz Ali Shah Rd, Block B2 Block B 2 Gulberg III, Lahore, Punjab 54000
Price: N/A
Total Reviews: 28 reviews
Average Review: 3.8
About: N/A
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipNL9GnQV_MJ2ysAhBncKZx8-f3bIl_a-Jo5KNLw=w252-h188-k-no, https://lh5.googleusercontent.com/p/AF1QipNL9GnQV_MJ2ysAhBncKZx8-f3bIl_a-Jo5KNLw=w252-h188-k-no, https://lh5.googleusercontent.com/p/AF1QipNS-nsZvaOE7Z-mLMlGqdf6VNRjfjHpinYB8c9O=w252-h448-k-no
Reviews:
  Username: Rana Zubair Khan
  Rating: 4/5
  Review: Nice cafe windmill. Good food, drinks, sheesha.  Good with friends.Service4.0Location4.0
  Username: Name Less
  Rating: 5/5
  Review: Best place for vacation and business, nice food and roomsRooms5.0Service5.0Location5.0Hotel highlightsGreat valueRoomsQuite luxuriousSafetyNice safety regardsFood & drinksQuite deliciousNote

Price element not found.
Data saved to CSV file: hotel_data.csv
Inserted data for hotel: Executive Lodge
Stored data for hotel: Executive Lodge
Address: F8VQ+4JW, Block M Gulberg III, Lahore, Punjab
Price: N/A
Total Reviews: 20 reviews
Average Review: 4.5
About: N/A
Facilities: 
Images: //lh5.googleusercontent.com/proxy/M_ClUf4FBQjcoVCEPYd7m-gwYjalVd6MyqLb3HuQF6tj5TUYZmCORdn1wM3SkBOj5HlBS1JTINxJd6RvODhQWGIyNcJ_2_6XwtxTzcMaLllrbqK6TwWvgJ16pLZcVNaw_kJ_WTkIhmQyUTKGo8zEyL8YauTcmA=w252-h142-k-no, //lh5.googleusercontent.com/proxy/M_ClUf4FBQjcoVCEPYd7m-gwYjalVd6MyqLb3HuQF6tj5TUYZmCORdn1wM3SkBOj5HlBS1JTINxJd6RvODhQWGIyNcJ_2_6XwtxTzcMaLllrbqK6TwWvgJ16pLZcVNaw_kJ_WTkIhmQyUTKGo8zEyL8YauTcmA=w252-h142-k-no, //lh4.googleusercontent.com/proxy/l2CEK5q6Xs33PEFGm0rnkyafmu7rt0Cu8daU4lZPkSg25InQdpexomu6Wum7zUT5c_yNc8v7BN5gv3MKPl3fDX1a6eXzgPwLLCEva4NrpotCwm9Uvx2Kg57FykMe024_xQfnKQiIzOMtMM72SC7uq1WZFahqQA=w252-h185-k-no
Reviews:
  Username: jamshaid AIE
  Rating: 5/5
  Review: The hotel's facilities were 

In [103]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name = soup.find('h1', class_='FNkAEc o4k8l')
        if name:
            hotel_name = name.text.strip()
            print("Name:", hotel_name)
            hotel_data['name'] = hotel_name
        else:
            print("Hotel name not found.")
            hotel_data['name'] = None 
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Chitrāl'
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

               

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        
        

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=chitral%20hotels&ts=CAESCgoCCAMKAggDEAAaUAoyEjAyJDB4MzhkYjUyOGQyMGViZDYyNzoweGY0YmY5MzZhZWRhNGUwZjoIQ2hpdHLEgWwSGhIUCgcI6A8QCBgBEgcI6A8QCBgCGAEyAhAAKgcKBToDUEtS&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgmjmoNqTFM_QBF8c3_VZoNSQBISCe-mLvrNoD9AEXxzfxULn1JAMAG6AQdyZXZpZXdz&qs=CAASBENDUT0gASgAOA1IAA&ved=0CAAQ5JsGahcKEwjApZzJzLGHAxUAAAAAHQAAAAAQTA')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1
max_hotels = 50

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    if len(all_links) >= max_hotels:
        all_links = all_links[:max_hotels]  # Limit the total links to max_hotels
        break
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '/html/body/c-wiz[2]/div/c-wiz/div[1]/div[1]/div[2]/div[2]/main/c-wiz/span/c-wiz/c-wiz[15]/div[1]/button/span')
        print("Found next page button.")
    except NoSuchElementException:
        
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[25]/div[1]/button[1]/span')
         #   print("Found alternate next page button.")
        except NoSuchElementException:
         #   # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'new_db' exists.
Collection 'hotel_data' exists in database 'new_db'.
Database 'new_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 10 links from page 1.
Found next page button.
Scraping page 2...
Collected 20 links from page 2.
Scraping page 3...
Collected 20 links from page 3.
All Scraped data from links:
1
Name: Kalash Guest House
Price element not found.
About section not found.
Inserted data for hotel: Kalash Guest House
Stored data for hotel: Kalash Guest House
Address: MMXM+MM8, Kalash, Brun, Chitral, Khyber Pakhtunkhwa
Price: N/A
Total Reviews: 1 review
Average Review: 4.0
About: N/A
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipMMj4yKwMUqxLzpE6O1aPgeOckcFKswQaKqEFyN=w252-h336-k-no, https://lh5.googleusercontent.com/p/AF1QipP3JIG39z8-0616yNpcF7QnqK9eLQEMN3zBnANW=w252-h336-k-no, https://lh5.googleusercontent.com/p/AF1QipNsO0EVj1mieNcFALDjOldtzcVJxUSS411Z6axW=w252-h336-k-no
Reviews:
  Username: Kalash Continental Hotel & R

Name: Hideaway Cottage Chitral
Price element not found.
Inserted data for hotel: Hideaway Cottage Chitral
Stored data for hotel: Hideaway Cottage Chitral
Address: HR93+9GC, Shahi qilla shainigar, drosh, Chitrāl, Chitral, Khyber Pakhtunkhwa 17200
Price: N/A
Total Reviews: 4.7 (69)Valley traditionally inhabited by the Kalash people, with a cultural museum, guesthouses & treks.

 1 hr 56 mins
Average Review: CloseView list
About: Check-in time: 14:00
Facilities: Pet-friendly
Images: 
Reviews:
https://www.google.com/travel/search?q=chitral%20hotels&ts=CAESCgoCCAMKAggDEAAaUAoyEjAyJDB4MzhkYjUyOGQyMGViZDYyNzoweGY0YmY5MzZhZWRhNGUwZjoIQ2hpdHLEgWwSGhIUCgcI6A8QCBgBEgcI6A8QCBgCGAEyAhAAKgcKBToDUEtS&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C7257085

Hotel name not found.
address not avalible
Images container not found.
Error extracting data from https://www.google.com/travel/search?q=chitral%20hotels&ts=CAESCgoCCAMKAggDEAAaUAoyEjAyJDB4MzhkYjUyOGQyMGViZDYyNzoweGY0YmY5MzZhZWRhNGUwZjoIQ2hpdHLEgWwSGhIUCgcI6A8QCBgBEgcI6A8QCBgCGAEyAhAAKgcKBToDUEtS&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgngD_KkzqtBQBGlCdvPfctRQBISCY0IF2IAP0JAEaUJ288OOlJAMAE&qs=CAASBENDUT0gASgAMihDaG9RMnBfR211VHVwYVRrQVJvTkwyY3ZNVEY1TTNsbVpHdHFkQkFDOA1IAA&ved=2ahUKEwjqwvf1zrGHAxXvAb8EHWjZD3oQyvcEegUIAxCWAQ: Message: no such elem

Name: Qashqar-Heights
Inserted data for hotel: Qashqar-Heights
Stored data for hotel: Qashqar-Heights
Address: near Jangbazar Shahi Masjid, Chitrāl, Chitral, Khyber Pakhtunkhwa 17200
Price: Rs 11,808
Total Reviews: 7 reviews
Average Review: 5.0
About: Check-out time: 12:00
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipOqNE1n46axdt0N6t64_drz5MgkYPErwRIWAQtK=w252-h315-k-no, https://lh5.googleusercontent.com/p/AF1QipOz37KCrooFNcxudHmG28VL0_G0Adp8Hgs0TvWn=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipPs1c7wbpUWnimWR8rxoWQin8rIYUI97vEntedA=w252-h189-k-no
Reviews:
  Username: Sikandar Shalmani
  Rating: 5/5
  Review: I recently stayed at Qashghar heights in Chitral and had a wonderful experience. The hotel is owned by Zia, a local from the area who is not only a great host but also fantastic company. He went out of his way to make sure that my stay was comfortable and enjoyable. The rooms were clean, spacious, and well-maintained, with all the necessary amenities

Name: Chinar Inn Chitral
Price element not found.
About section not found.
Inserted data for hotel: Chinar Inn Chitral
Stored data for hotel: Chinar Inn Chitral
Address: VQ2Q+G29, Shahi Bazar, Chitrāl, Chitral, Khyber Pakhtunkhwa
Price: N/A
Total Reviews: 24 reviews
Average Review: 3.9
About: N/A
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipPnjNxLyWpjg00i42gt5aKhYr7ugdQF6saXXFk9=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipPnjNxLyWpjg00i42gt5aKhYr7ugdQF6saXXFk9=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipNRuKwJYO2ylOMhGhs9-COst2nKXjdDUq500EhC=w252-h189-k-no
Reviews:
  Username: Mehtab Uddin
  Rating: 5/5
  Review: Chinar Inn Hotel Chitral Lower was very busy and Famous hotel in Chitral. But recently the building was handed over to Alkhidmat Foundation Chitral. Now Alkhidmat Hospital Chitral Lower is fully functional and providing good medical facilities to the patients of upper and lower Chitral.
  Username: Mouzam Younas
  Rating: 4/5
  Rev

...

Name: Chitral Inn Resort (Kalash Valley)
Inserted data for hotel: Chitral Inn Resort (Kalash Valley)
Stored data for hotel: Chitral Inn Resort (Kalash Valley)
Address: MMM4+G5J, Kalash Valley Bamburat Krakal, Valley Bamburat, Kalash, Chitrāl, Chitral, Khyber Pakhtunkhwa 17200
Price: Rs 12,180
Total Reviews: 35 reviews
Average Review: 4.6
About: Check-in time: 14:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeWi-Fifree, InternetWi-FifreeServicesFront desk24-hourFull-service laundryParking & transportParkingfreeTransferLocal shuttleFood and drinkRoom serviceBreakfastfreePoolsNo poolsNo hot tubWellnessNo fitness centreNo spa
Images: //lh5.googleusercontent.com/proxy/aex32boUEMu4yuPlbDBvLN5l4g2dwwCJOI0aRxDOMZHODYi3NhbMvnNqkqjks96Ud1glD-_kVISU9cW1axEey3vhDNI50erYKsLiDo6uOUTZAHJie5SpTugXDpJ6Xc96gxqAVPs06lYO6AGKQmaGEWoernK20Pw=w252-h189-k-no, //lh5.googleusercontent.com/proxy/flEVs6v_kUYoiJT3fiCcYwLzj0TB_B7AUV--FlMnq-7X9FvE9NfTSAvZ8ryz0EEAjfbWe0dG584bbKGiqU7CKt-17dwfsa6uTipazv6bI

Name: Chitral Inn Hotel
Price element not found.
Inserted data for hotel: Chitral Inn Hotel
Stored data for hotel: Chitral Inn Hotel
Address: Polo Ground, Road, Jamuxi, Chitrāl, Chitral, Khyber Pakhtunkhwa 72000
Price: N/A
Total Reviews: 147 reviews
Average Review: 4.1
About: Check-in time: 14:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeAir conditioning, InternetWi-FifreeServicesFront desk24-hourFull-service laundryParking & transportParkingfreeTransferRoomsAir conditioningFood and drinkRestaurantBreakfastfreePoolsNo poolsNo hot tubWellnessNo fitness centreNo spa
Images: //lh5.googleusercontent.com/proxy/XxiBsPiNraKmwIR8sq-ZQ_22kuZ0AzKuMvg4BW0uNjkZ5QDWG-w0eAqsFokEJCiDlo5etxgH4_xlT8ck3oDH3UcBSo6X5_9rxYgy9Y1yljmRgia-K4Yj2k2Vo-k5LyHK4IomIR8qBcuLpTJwJ7FIZjRkVvaaa1c=w252-h189-k-no, //lh4.googleusercontent.com/proxy/JKHH_4COiMQxGk6vkBHvTc83W1qOqaIDYfisIHRgA_VPU7lqe94GIUYgEfEBCmjzqg99mi-7K7ibvZuDyjOqlcr3krQ9c39Li0Iaif4MlVajB-gijUpJHNN9iMOQ8UJJlBCuFEOpN2Uiizhj3YmNyIX9I

Name: Gahirat Castle
Price element not found.
Inserted data for hotel: Gahirat Castle
Stored data for hotel: Gahirat Castle
Address: MQ83+CXF, Gabhirat, Chitrāl, Chitral, Khyber Pakhtunkhwa
Price: N/A
Total Reviews: 64 reviews
Average Review: 4.8
About: Check-in time: 14:00
Facilities: ParkingfreeBreakfastfreeWi-FiRestaurant, InternetWi-FiServicesFront desk24-hourFull-service laundryParking & transportParkingfreeLocal shuttleFood and drinkRestaurantRoom serviceBreakfastfreePoolsNo poolsNo hot tubWellnessNo fitness centreNo spa
Images: //lh4.googleusercontent.com/proxy/TW50EarDrp2iSDCXqNMN-UMTX2e58tfV0QCVHMwkrOPDZEr9-wbovFHKpKjmgewHdf9t3zY0EygOZMQhgeKGZCnzrFkOHaCxk4T7nQpeflAQ5aZI_2tNH-YbWfbkYUVnLRj3m1ZeARmgnANIuHjThnCF-JYU43U=w252-h336-k-no, https://lh5.googleusercontent.com/p/AF1QipNWDu1Y3PMoy5muw1tI-gVjsude4r-Mpfp1dMp3=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipOuSBl2jThcoyNKdZCiTOD3Yj_-8UOeMiz0hXtW=w252-h189-k-no
Reviews:
  Username: Samina Halai
  Rating: 5/5
  Review

Name: Foreigner Tourist Inn
Inserted data for hotel: Foreigner Tourist Inn
Stored data for hotel: Foreigner Tourist Inn
Address: MMXM+7MG, Bamboret Valley Road, Kalash, Brun, Chitral, Khyber Pakhtunkhwa
Price: Rs 13,749
Total Reviews: 15 reviews
Average Review: 3.5
About: Check-in time: 14:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeRestaurant, InternetWi-FifreeServicesFront desk24-hourFull-service laundryPoolsNo poolsNo hot tubWellnessNo fitness centreNo spaFood and drinkRestaurantRoom serviceBreakfastfreeChildrenChild-friendlyParking & transportParkingfreeTransferLocal shuttle
Images: https://lh5.googleusercontent.com/p/AF1QipPnkQrLjji4_y-J9q2WzaRq1eDXC7QWNrU4rLvs=w252-h252-k-no, https://lh5.googleusercontent.com/p/AF1QipPucFKhAD0FVZb25uvAUDMCcM-su-8ub8-ndJTL=w252-h252-k-no, //lh4.googleusercontent.com/proxy/Ig_ndGrHANIG2zkwBOS2H6BQAO623NTJLHrSqO0fe9X9ufpgtUIn9q1GDdb4XbKyLTB4rwVJ6HEzp3izv_y8gKRI67MmfVlUq_zWzrYcJfgIkUr2nAJICK55hriHh8s0nrd4XKR_ZGSdNx7UEoKWJLzJr

Name: PTDC Motel Chitral
Price element not found.
Inserted data for hotel: PTDC Motel Chitral
Stored data for hotel: PTDC Motel Chitral
Address: VQ5Q+P4P, Shahi Bazar, Chitrāl, Chitral, Khyber Pakhtunkhwa
Price: N/A
Total Reviews: 487 reviews
Average Review: 4.0
About: Check-in time: 00:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeAir conditioningWi-Fi, InternetWi-FiServicesFront desk24-hourFull-service laundryParking & transportParkingfreeTransferLocal shuttlePetsNo petsFood and drinkRestaurantRoom serviceBreakfastfreePoolsNo poolsNo hot tubWellnessNo fitness centreNo spaRoomsAir conditioning
Images: https://lh5.googleusercontent.com/p/AF1QipNwhcBlx4pt6Wm3Vho5uQSEYpzjb6zC5YYjPXE=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipNwhcBlx4pt6Wm3Vho5uQSEYpzjb6zC5YYjPXE=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipM3zEH60A7C8mCCixgSxrXzNr45CWl_7m7yYQzy=w252-h189-k-no
Reviews:
  Username: usman Ahmed
  Rating: 3/5
  Review: It looked fine from outside whe

In [106]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name = soup.find('h1', class_='FNkAEc o4k8l')
        if name:
            hotel_name = name.text.strip()
            print("Name:", hotel_name)
            hotel_data['name'] = hotel_name
        else:
            print("Hotel name not found.")
            hotel_data['name'] = None 
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Gilgit'
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

               

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        
        

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=gilgit%20hotels&ts=CAESCgoCCAMKAggDEAAaTwoxEi8yJTB4MzhlNjQ5ZTM2NDI1NDNiMToweDQwZmQwY2EzY2ExNzI4MmI6BkdpbGdpdBIaEhQKBwjoDxAIGAESBwjoDxAIGAIYATICEAAqBwoFOgNQS1I&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgngD_KkzqtBQBGlCdvPfctRQBISCY0IF2IAP0JAEaUJ288OOlJAMAG6AQdyZXZpZXdz&qs=CAASBENHdz0gACgAOA1IAA&ved=0CAAQ5JsGahcKEwiY24P60bGHAxUAAAAAHQAAAAAQVA')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1
max_hotels = 110

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    if len(all_links) >= max_hotels:
        all_links = all_links[:max_hotels]  # Limit the total links to max_hotels
        break
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '/html/body/c-wiz[2]/div/c-wiz/div[1]/div[1]/div[2]/div[2]/main/c-wiz/span/c-wiz/c-wiz[7]/div[1]/button/span')
        print("Found next page button.")
    except NoSuchElementException:
        
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[25]/div[1]/button[1]/span')
         #   print("Found alternate next page button.")
        except NoSuchElementException:
         #   # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'new_db' exists.
Collection 'hotel_data' exists in database 'new_db'.
Database 'new_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 2 links from page 1.
Found next page button.
Scraping page 2...
Collected 20 links from page 2.
Scraping page 3...
Collected 20 links from page 3.
Scraping page 4...
Collected 20 links from page 4.
Scraping page 5...
Collected 20 links from page 5.
Scraping page 6...
Collected 20 links from page 6.
Scraping page 7...
Collected 20 links from page 7.
All Scraped data from links:
1
Name: Countryside Resort - Twin Room with Private Bathroom
address not avalible
Price element not found.
Inserted data for hotel: Countryside Resort - Twin Room with Private Bathroom
Stored data for hotel: Countryside Resort - Twin Room with Private Bathroom
Address: no address
Price: N/A
Total Reviews: 14–19 Aug
Average Review: CloseView list
About: DetailsSituated in Gilgit, Countryside Resort features accommodation with seating area. This

Name: Hotel 1947
Price element not found.
Inserted data for hotel: Hotel 1947
Stored data for hotel: Hotel 1947
Address: Chappra Naran Naran Naran, 21210
Price: N/A
Total Reviews: 4.1 (36)0.3 km away
Average Review: CloseView list
About: Check-out time: 12:00
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipPod6pDqM-hqslk8dX_8DPrIssShPEI9xykvoDW=w252-h448-k-no?w=1024
Reviews:
https://www.google.com/travel/search?q=gilgit%20hotels&ts=CAESCgoCCAMKAggDEAAaTwoxEi8yJTB4MzhlNjQ5ZTM2NDI1NDNiMToweDQwZmQwY2EzY2ExNzI4MmI6BkdpbGdpdBIaEhQKBwjoDxAIGAESBwjoDxAIGAIYATICEAAqBwoFOgNQS1I&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C7

Name: Capital Lodge Gilgit
About section not found.
Inserted data for hotel: Capital Lodge Gilgit
Stored data for hotel: Capital Lodge Gilgit
Address: •
Price: Rs 16,213
Total Reviews: 51 reviews
Average Review: 3.9
About: N/A
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipNhbaXcj4x7cWV52dsQ8gm33IL_IrWRDNxk1xyM=w252-h349-k-no, https://lh5.googleusercontent.com/p/AF1QipPfMaeOLjjXZryoyyYVYFU6naYMHEX0XsMWWewA=w252-h153-k-no, https://lh5.googleusercontent.com/p/AF1QipMOaTRdGIl16JuLRmJvTcx__jcglvF940L8qbCn=w252-h336-k-no
Reviews:
  Username: ali naqvi
  Rating: 5/5
  Review: It was a very good experience. My family is very happy in this hotel. There is no need for any spice for us. You guys also go and enjoyRooms5.0Service5.0Location4.0
  Username: Avaix
  Rating: 5/5
  Review: This hotel  is a new addition to the hospitality industry in Gilgit, located at a very convenient  place, easy access to go anywhere.Due to its food quality, service standers and its locality it is th

Name: Oak Residency
address not avalible
Price element not found.
Inserted data for hotel: Oak Residency
Stored data for hotel: Oak Residency
Address: no address
Price: N/A
Total Reviews: 4–11 Aug
Average Review: CloseView list
About: DetailsWith a stay at Oak Residency  in Gilgit, you'll be within a 5-minute drive of Lalik Jan Stadium and City Park.  This guesthouse is 3.1 mi (4.9 km) from Karakoram International University and 3.5 mi (5.6 km) from Uprising Memorial.  Make yourself at home in one of the air-conditioned guestrooms. Complimentary wireless internet access is available to keep you connected. Private bathrooms have rainfall showerheads and complimentary toiletries.Website
Facilities: Entire house, Sleeps 2, 1 bedroom, 1 bathroom, Free breakfast, Smoke-free, Free parking, Free Wi-Fi
Images: https://lh4.googleusercontent.com/proxy/ypphT8MUatvmCgoWH7mmGmdci3V4VfVdZNzZ1KrBF-WI57guee7GpI2Oo3XKXqFF9VHS3X5vZmBOFYvTXcLZNJE_zcHytT-GL1HsRTN-Sp_ohW9tza6vZAkAOcacValF6EAMeA3Pw901uqPTLq

Name: Riverdale Resort - Queen Room with Pool View
address not avalible
Price element not found.
Inserted data for hotel: Riverdale Resort - Queen Room with Pool View
Stored data for hotel: Riverdale Resort - Queen Room with Pool View
Address: no address
Price: N/A
Total Reviews: 14–19 Aug
Average Review: CloseView list
About: DetailsFeaturing mountain views, Riverdale Resort in Gilgit features accommodation, a garden, a shared lounge, a terrace and a restaurant. Both WiFi and private parking are accessible at the lodge free of charge. The pool with a view is a top feature of this double room. This air-conditioned double room is comprised of a flat-screen TV with cable channels, a private bathroom as well as a terrace with garden views. The unit has 1 bed.Website
Facilities: Entire house, Sleeps 3, 1 bedroom, 1 bathroom, 1 bed, Air conditioning, Airport shuttle, Child-friendly, Cot, Fitness centre, Heating, Ironing board, Kitchen, Outdoor grill, Outdoor pool, Pet-friendly, Smoke-free, 

...

Name: Indus Lodges Gilgit
Inserted data for hotel: Indus Lodges Gilgit
Stored data for hotel: Indus Lodges Gilgit
Address: River View Rd, Sonikot, Gilgit, Gilgit-Baltistan
Price: Rs 7,000
Total Reviews: 2,099 reviews
Average Review: 4.8
About: Overlooking the Gilgit River, this relaxed hotel is 2 km from Gilgit Airport, 4 km from Karakoram International University and 3 km from the KIU View Point, for panoramic Himalaya views.… MoreThe warm, wood-panelled rooms offer TVs, Wi-Fi, minifridges and kettles, as well as air conditioning, and en suite facilities with bucket showers. Some rooms have balconies.The furnished rooftop terrace offers river views. A breakfast buffet is available.Check-in time: 14:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeAir conditioning, InternetWi-FifreeServicesFront desk24-hourFull-service laundryParking & transportParkingfreeTransferLocal shuttleRoomsAir conditioningFood and drinkRestaurantRoom serviceBreakfastfreePoolsNo poolsNo hot t

Name: Rupal Inn
Inserted data for hotel: Rupal Inn
Stored data for hotel: Rupal Inn
Address: •
Price: Rs 9,596
Total Reviews: 635 reviews
Average Review: 3.9
About: Check-in time: 14:00Check-out time: 11:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeRestaurant, InternetWi-FifreeServicesFront desk24-hourFull-service laundryPoolsNo poolsNo hot tubWellnessNo fitness centreNo spaFood and drinkRestaurantRoom serviceBreakfastfreeChildrenChild-friendlyParking & transportParkingfreeTransferLocal shuttle
Images: //lh4.googleusercontent.com/proxy/7e6ynC3ebJuieG85npzJDf5Fs9wY5N5bn-OoG7ZrunoZr1EYezexs6ESUx9z8iuKufd_eEszQC1yRRwLo35XmejQVXK0GtpaLI9GYqsxmoFNpYmwW09mUabHd2QeEGWkuxon66f3220oxVr0oASI88hbxEjXFA=w252-h168-k-no, https://lh5.googleusercontent.com/p/AF1QipNKp1SZ4Pj42GxCaqIki7tDy0bPuwCAC3kydTu1=w252-h156-k-no, https://lh5.googleusercontent.com/p/AF1QipMKk0rLuEnRIU2dSrTivvLd2MFp_ZU8jyoJeCDA=w252-h189-k-no
Reviews:
  Username: Nick Wildsmith
  Rating: 2/5
  Review: Average hotel, it is ok for

Name: ISLE OF HIGHLAND TOURS GUEST HOUSE
Hotel ISLE OF HIGHLAND TOURS GUEST HOUSE already exists in the database. Skipping insertion.
Stored data for hotel: ISLE OF HIGHLAND TOURS GUEST HOUSE
Address: River View Rd, Gilgit, Gilgit-Baltistan 15100
Price: Rs 7,000
Total Reviews: 81 reviews
Average Review: 4.3
About: InternetWi-FifreeWi-Fi in public areasServicesFront desk24-hourFull-service laundryWake up callsWellnessNo fitness centreNo spaRoomsAir conditioningBathroomsPrivate bathroomShower
Facilities: ParkingfreeBreakfastfreeWi-FifreeAir conditioning, InternetWi-FifreeWi-Fi in public areasServicesFront desk24-hourFull-service laundryWake up callsWellnessNo fitness centreNo spaRoomsAir conditioningBathroomsPrivate bathroomShowerFood and drinkRoom serviceBreakfastfreePoolsNo poolsNo hot tubParking & transportParkingfreeCar rental onsiteLanguages spokenEnglishHindi
Images: https://lh5.googleusercontent.com/p/AF1QipOQcUHr7tU3WeyxqdtHwLUK48Q28a0kwdDja4eC=w252-h252-k-no, https://lh5.googleu

Name: Hotel Oasis International
Inserted data for hotel: Hotel Oasis International
Stored data for hotel: Hotel Oasis International
Address: W937+GRP, Opposite Gilgit Baltistan Assembly, Jutial, Gilgit, Gilgit-Baltistan 15100
Price: Rs 7,421
Total Reviews: 140 reviews
Average Review: 4.4
About: Check-in time: 14:00Check-out time: 11:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeRestaurant, InternetWi-FifreeServicesFront desk24-hourFull-service laundryParking & transportParkingfreeLocal shuttleFood and drinkRestaurantRoom serviceBreakfastfreePoolsNo poolsNo hot tubWellnessNo fitness centreNo spa
Images: https://lh5.googleusercontent.com/p/AF1QipPS9h-8UMiFk8Ahxx6wYQcH0qsdvbb1CTp3ligc=w252-h168-k-no, https://lh5.googleusercontent.com/p/AF1QipPS9h-8UMiFk8Ahxx6wYQcH0qsdvbb1CTp3ligc=w252-h168-k-no, https://lh5.googleusercontent.com/p/AF1QipPULbaeyLgMS_4x0KnfWZ1IW8rKKP4Ii8oXQWN_=w252-h168-k-no
Reviews:
  Username: abdullah malik
  Rating: 2/5
  Review: The room was spacious with inverter AC

Name: Park Hotel Gilgit
Inserted data for hotel: Park Hotel Gilgit
Stored data for hotel: Park Hotel Gilgit
Address: •
Price: Rs 7,475
Total Reviews: 1,219 reviews
Average Review: 4.1
About: Check-in time: 14:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeAir conditioningWi-Fi, InternetWi-FiServicesFront desk24-hourFull-service laundryPoolsNo poolsNo hot tubWellnessNo fitness centreNo spaFood and drinkRestaurantRoom serviceBreakfastfreeChildrenChild-friendlyParking & transportParkingfreeTransferLocal shuttleRoomsAir conditioning
Images: //lh4.googleusercontent.com/proxy/2w8gqM8Bj295Yr5yKE2je6dBzPbyoDoRymF74RNJE0YcyFx6JUQgeNv7NzdPpcv1_ePmpZdDPm3sQ7YZ9Xb4GcTfZhAQKkvvhYBw-GsNpdZ5NAkvNWzAOBNja1NzJj6QcF5DVkqQwUcmLzWmCAFV1yUznuQ8Yg=w252-h168-k-no, https://lh5.googleusercontent.com/p/AF1QipOrAz7FFloFmKYrM2p29Olen-NgZ2PbQn73vv4X=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipMaQpsi5-AByCwut0sm0ukAh3kcAnZqH25cYdfb=w252-h189-k-no
Reviews:
  Username: batool waqar
  Rating

In [13]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name = soup.find('h1', class_='FNkAEc o4k8l')
        if name:
            hotel_name = name.text.strip()
            print("Name:", hotel_name)
            hotel_data['name'] = hotel_name
        else:
            print("Hotel name not found.")
            hotel_data['name'] = None 
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Murree '
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

               

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        
        

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=murree%20hotels&ts=CAESCgoCCAMKAggDEAAaTwoxEi8yJTB4MzhkZmQ3MTU3NzYwOTdhOToweDE3YjJlMWQ2YmZiOGUxOTA6Bk11cnJlZRIaEhQKBwjoDxAIGAESBwjoDxAIGAIYATICEAAqBwoFOgNQS1I&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgnQPVyue-JAQBF_me-QcEtSQBISCVa9ReMwCEFAEX-Z79AUZ1JAMAE&qs=CAESBENJNEMgASgAOA1IAA&ved=0CAAQ5JsGahcKEwjIn4Puz7KHAxUAAAAAHQAAAAAQHw')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1
max_hotels = 280

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    if len(all_links) >= max_hotels:
        all_links = all_links[:max_hotels]  # Limit the total links to max_hotels
        break
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[23]/div[1]/button[1]/span')
        print("Found next page button.")
    except NoSuchElementException:
        
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[25]/div[1]/button[1]/span')
         #   print("Found alternate next page button.")
        except NoSuchElementException:
         #   # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'new_db' exists.
Collection 'hotel_data' exists in database 'new_db'.
Database 'new_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 18 links from page 1.
Found next page button.
Scraping page 2...
Collected 18 links from page 2.
Found next page button.
Scraping page 3...
Collected 18 links from page 3.
Found next page button.
Scraping page 4...
Collected 20 links from page 4.
Scraping page 5...
Collected 20 links from page 5.
Scraping page 6...
Collected 20 links from page 6.
Scraping page 7...
Collected 20 links from page 7.
Scraping page 8...
Collected 20 links from page 8.
Scraping page 9...
Collected 20 links from page 9.
Scraping page 10...
Collected 20 links from page 10.
Scraping page 11...
Collected 20 links from page 11.
Scraping page 12...
Collected 20 links from page 12.
Scraping page 13...
Collected 20 links from page 13.
Scraping page 14...
Collected 20 links from page 14.
Scraping page 15...
Collected 20 links from page 15.
All Scr

Name: Grand Heights - Deluxe Double Room
address not avalible
Price element not found.
Inserted data for hotel: Grand Heights - Deluxe Double Room
Stored data for hotel: Grand Heights - Deluxe Double Room
Address: no address
Price: N/A
Total Reviews: Sleeps 40.5 km away
Average Review: CloseView list
About: DetailsSituated in Murree in the Punjab Region region, Grand Heights has a garden. There is an in-house restaurant, plus free private parking and free WiFi are available. Boasting family rooms, this property also provides guests with a terrace. This double room features heating, a flat-screen TV and a balcony. The unit has 1 bed.Website
Facilities: Entire apartment, Sleeps 2, 1 bedroom, 1 bathroom, 1 bed, Balcony, Child-friendly, Heating, Smoke-free, Cable TV, Washing machine, Free parking, Free Wi-Fi
Images: https://lh5.googleusercontent.com/proxy/KORzldlQYvemgusJ_-dptP1rHwf7q337tQg_le22xs4IXKKR6nlb48HnjoibpkmJix79XyeCYzCyNPztFlUvwFXXctBM6bUmRyl2UI-4FWhRIefsruJ9svXv2LEluxjAyQjqFAP9

Name: Resort One Murree - Three-Bedroom Villa
address not avalible
Price element not found.
Inserted data for hotel: Resort One Murree - Three-Bedroom Villa
Stored data for hotel: Resort One Murree - Three-Bedroom Villa
Address: no address
Price: N/A
Total Reviews: 22–28 Jul
Average Review: CloseView list
About: DetailsBoasting a garden and views of garden, Resort One Murree is a recently renovated villa located in Murree, 43 km from Lake View Park. This property offers access to a terrace, table tennis, free private parking and free WiFi. This villa's special feature is the spa bath. This spacious villa comprises 2 living rooms, 3 separate bedrooms and 4 bathrooms with a shower and free toiletries. Guests will find a stovetop, a refrigerator, kitchenware and an oven in the kitchen. The villa also provides guests with a barbecue. Featuring a terrace with garden views, this villa also provides a washing machine and a flat-screen TV with cable channels. The unit offers 8 beds.Website
Fac

Name: Navid's Holiday Resort and Hotel, Murree - Two-Bedroom Apartment
address not avalible
Price element not found.
Inserted data for hotel: Navid's Holiday Resort and Hotel, Murree - Two-Bedroom Apartment
Stored data for hotel: Navid's Holiday Resort and Hotel, Murree - Two-Bedroom Apartment
Address: no address
Price: N/A
Total Reviews: 25 Jul – 1 Aug
Average Review: CloseView list
About: DetailsOffering a terrace and city view, Navid's Holiday Resort and Hotel, Murree is situated in Ghora Gali, 49 km from Shah Faisal Mosque and 39 km from Lake View Park. This property offers access to a patio and free private parking. Featuring a private entrance, this spacious apartment also consists of 2 separate bedrooms, 2 bathrooms, a living room and a seating area. The fully equipped kitchen features a refrigerator, kitchenware, a microwave and a tea and coffee maker. Boasting a balcony with mountain views, this apartment also provides a washing machine and a flat-screen TV. The unit offers 2 

Name: Roof Top Resort - Two-Bedroom House
address not avalible
Price element not found.
Inserted data for hotel: Roof Top Resort - Two-Bedroom House
Stored data for hotel: Roof Top Resort - Two-Bedroom House
Address: no address
Price: N/A
Total Reviews: 22–28 Jul
Average Review: CloseView list
About: DetailsLocated in Murree, Roof Top Resort provides accommodation with free WiFi and seating area. The property features garden and city views. Featuring family rooms, this property also provides guests with a terrace. Featuring a private entrance, this holiday home is comprised of 1 living room, 2 separate bedrooms and 2 bathrooms with a shower and a hairdryer. Guests will find a stovetop, a refrigerator, kitchenware and an oven in the kitchen. The holiday home also has a barbecue. Boasting a terrace with garden views, this holiday home also offers soundproof walls and a flat-screen TV. The unit offers 3 beds.Website
Facilities: Entire house, Sleeps 4, 2 bedrooms, 2 bathrooms, 3 beds, Balc

...

Name: Hotel Cecil Homes
Inserted data for hotel: Hotel Cecil Homes
Stored data for hotel: Hotel Cecil Homes
Address: •
Price: Rs 26,053
Total Reviews: 808 reviews
Average Review: 4.2
About: Check-in time: 14:00Check-out time: 12:00
Facilities: ParkingfreeWi-FifreeBreakfastextra chargeRestaurant, InternetWi-FifreeServicesFront desk24-hourFull-service laundryParking & transportParkingfreeAccessibilityAccessiblePetsNo petsFood and drinkRestaurantRoom serviceBreakfastextra chargePoolsNo poolsNo hot tubWellnessNo fitness centreNo spaRoomsNo air conditioningKitchen in some rooms
Images: //lh5.googleusercontent.com/proxy/ITnzzjvBRimXM3f6ddgGzFMOIJH2iF5l1MiWFdZ1K1W6iaXGQWBve3N3ZdNpJPTKOjDnp2VZQPdgUwvbTLhzKz6_CA9SzPpLI-5RZq0oGwlrCefQnsgvWdFuxstEkoksas52LwWFs1A9Pn9abk1LntExVItv7g=w252-h190-k-no, //lh4.googleusercontent.com/proxy/Zm8muWgKBIxt1SUFpOhhduWEptTEdUc8bhqVv0gHIq2gpFenOicsASlQSgkjKtcX3aWz7LkWZrv93cgvKslLzcW_v3A7yr5o_tG8cEVU4hdU7QDGz5IkGZ-EXdVh0SF0_albdqUkKfeSDefHdQioqJGEIH-JQ5M=w252-h168

Name: Midway - Apartment - Ground Floor
address not avalible
Inserted data for hotel: Midway - Apartment - Ground Floor
Stored data for hotel: Midway - Apartment - Ground Floor
Address: no address
Price: Rs 6,333
Total Reviews: Rs 6,333 total1 night with taxes + fees
Average Review: CloseView list
About: DetailsSituated 44 km from Lake View Park, Midway offers accommodation with a balcony, as well as a garden and barbecue facilities. Boasting a shared kitchen, this property also provides guests with a children's playground. Featuring 2 bedrooms and 2 bathrooms, this apartment offers a living room and terrace where you can relax. The apartment's kitchen is available for cooking and storing food. This apartment offers a washing machine, a flat-screen TV and a balcony. The unit has 4 beds.Website
Facilities: Entire apartment, Sleeps 5, 2 bedrooms, 2 bathrooms, 4 beds, Balcony, Child-friendly, Ironing board, Kitchen, Smoke-free, Cable TV, Washing machine, Wheelchair accessible, Free parkin

Name: Hotel Metropole Murree
Inserted data for hotel: Hotel Metropole Murree
Stored data for hotel: Hotel Metropole Murree
Address: Plot#51/52, W95X+432 Hall, road, Murree, Rawalpindi, Punjab 47150
Price: Rs 13,430
Total Reviews: 1,004 reviews
Average Review: 4.0
About: On a hillside in the foothills of the Himalayas, this informal hotel is 10 minutes away on foot from the Mall of Murree and 3 km from the Pindi Point Chair Lift. The E-75 Expressway is 6 km away.… MoreThe warm, relaxed rooms feature Wi-Fi, TVs and minifridges, as well as coffeemakers. Upgraded rooms add sitting areas; suites have separate living rooms. Some quarters offer mountain views. Room service is available.Amenities include a restaurant, a BBQ area and secured parking, along with breakfast.Check-in time: 13:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeAir conditioning, InternetWi-FifreePolicies & paymentsCredit cardsDebit cardsNFC mobile paymentsCashChildrenChild-friendlyPoolsNo poolsNo ho

Name: Resort One Murree - Standard Villa
address not avalible
Inserted data for hotel: Resort One Murree - Standard Villa
Stored data for hotel: Resort One Murree - Standard Villa
Address: no address
Price: Rs 17,811
Total Reviews: Rs 17,811 total1 night with taxes + fees
Average Review: CloseView list
About: DetailsBoasting a garden and views of garden, Resort One Murree is a recently renovated villa located in Murree, 43 km from Lake View Park. This property offers access to a terrace, table tennis, free private parking and free WiFi. Boasting a private entrance, this spacious villa also includes 1 living room, 2 separate bedrooms and 3 bathrooms with a shower. Featuring a terrace with mountain views, this villa also offers a washing machine and a flat-screen TV with cable channels. The unit has 6 beds.Website
Facilities: Entire villa, Sleeps 10, 2 bedrooms, 3 bathrooms, 6 beds, Air conditioning, Airport shuttle, Balcony, Child-friendly, Cot, Fitness centre, Heating, Ironing board, K

Name: GOHO Rooms | Murree
Price element not found.
Inserted data for hotel: GOHO Rooms | Murree
Stored data for hotel: GOHO Rooms | Murree
Address: VCQ4+HG9, Islamabad - Murree Expy, Murree, Rawalpindi, Khyber Pakhtunkhwa 47150
Price: N/A
Total Reviews: 5 reviews
Average Review: 3.4
About: Check-out time: 12:00
Facilities: Wi-FifreeAir conditioning, InternetWi-FifreeWi-Fi in public areasBathroomsPrivate bathroomShowerRoomsAir conditioningKitchen in some roomsRefrigerator in some roomsMicrowave in some roomsCoffee maker in some rooms
Images: //lh3.googleusercontent.com/proxy/cBVsxfSWGXpBvciFKNeeIjpvdyogc4Jfwr-UgvGe6jrpYHIicfhmXtTOmkNgI8XQV-mFwMcskDBAJFvfGU_3qtD9C4b_oKXR1padkxgFAw_uKcvIpf0jYBTFlWf0FhBgNawD6XkSDHNlb1wp9lRkaX6Y6_mOcw=w252-h336-k-no, //lh3.googleusercontent.com/proxy/cBVsxfSWGXpBvciFKNeeIjpvdyogc4Jfwr-UgvGe6jrpYHIicfhmXtTOmkNgI8XQV-mFwMcskDBAJFvfGU_3qtD9C4b_oKXR1padkxgFAw_uKcvIpf0jYBTFlWf0FhBgNawD6XkSDHNlb1wp9lRkaX6Y6_mOcw=w252-h336-k-no, https://lh5.googleusercontent.com/p

In [16]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name = soup.find('h1', class_='FNkAEc o4k8l')
        if name:
            hotel_name = name.text.strip()
            print("Name:", hotel_name)
            hotel_data['name'] = hotel_name
        else:
            print("Hotel name not found.")
            hotel_data['name'] = None 
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Multan '
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

               

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        
        

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=multan%20%20hotels&ts=CAESCgoCCAMKAggDEAAaTwoxEi8yJTB4MzkzYjMxNTc3OGRlYTdkOToweGJhZDcyZmM3NGU1NWQ0MmY6Bk11bHRhbhIaEhQKBwjoDxAIGAESBwjoDxAIGAIYATICEAAqBwoFOgNQS1I&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgnQPVyue-JAQBF_me-QcEtSQBISCVa9ReMwCEFAEX-Z79AUZ1JAMAG6AQdyZXZpZXdz&qs=CAASBENHdz0gACgAOA1IAA&ved=0CAAQ5JsGahcKEwiwjtmm47KHAxUAAAAAHQAAAAAQSw')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1
max_hotels = 115

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    if len(all_links) >= max_hotels:
        all_links = all_links[:max_hotels]  # Limit the total links to max_hotels
        break
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '/html/body/c-wiz[2]/div/c-wiz/div[1]/div[1]/div[2]/div[2]/main/c-wiz/span/c-wiz/c-wiz[14]/div[1]/button[1]/span')
        print("Found next page button.")
    except NoSuchElementException:
        
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[25]/div[1]/button[1]/span')
         #   print("Found alternate next page button.")
        except NoSuchElementException:
         #   # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'new_db' exists.
Collection 'hotel_data' exists in database 'new_db'.
Database 'new_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 9 links from page 1.
Found next page button.
Scraping page 2...
Collected 20 links from page 2.
Scraping page 3...
Collected 20 links from page 3.
Scraping page 4...
Collected 20 links from page 4.
Scraping page 5...
Collected 20 links from page 5.
Scraping page 6...
Collected 20 links from page 6.
Scraping page 7...
Collected 20 links from page 7.
All Scraped data from links:
1
Name: Hotel Decent Lodge
Inserted data for hotel: Hotel Decent Lodge
Stored data for hotel: Hotel Decent Lodge
Address: Humayun Road, H # 370 ,Link Road, Chungi No.9 Flyover, opp. Metro Bridge, near Chowk, Mohalla Muhammadi, Multan, Punjab 66000
Price: Rs 23,960
Total Reviews: 136 reviews
Average Review: 4.4
About: Set on a side street, this modest guesthouse is 1 km from the Tomb of Hazrat Shah Rukn-e-Alam and 2 km from Shah Shams Park. Mul

Name: Synergy Rooms
Price element not found.
Inserted data for hotel: Synergy Rooms
Stored data for hotel: Synergy Rooms
Address: M A Jinnah Road Near MashAllah Chowk Multan Punjab Region, 60000
Price: N/A
Total Reviews: 3.9 (1,285)Free breakfast, Wi-Fi and parking0.8 km away
Average Review: CloseView list
About: Check-in time: 14:00
Facilities: 
Images: 
Reviews:
https://www.google.com/travel/search?q=multan%20%20hotels&ts=CAESCgoCCAMKAggDEAAaTwoxEi8yJTB4MzkzYjMxNTc3OGRlYTdkOToweGJhZDcyZmM3NGU1NWQ0MmY6Bk11bHRhbhIaEhQKBwjoDxAIGAESBwjoDxAIGAIYATICEAAqBwoFOgNQS1I&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72

Name: PC Pink Room 03366386547
address not avalible
Price element not found.
Inserted data for hotel: PC Pink Room 03366386547
Stored data for hotel: PC Pink Room 03366386547
Address: no address
Price: N/A
Total Reviews: 1–2 Aug
Average Review: CloseView list
About: DetailsGuests Are Gift Of God, We Warmheartedly Welcome Guests All Around the World. We also provide them transportation if needed. And cook delicious Pakistani Dishes whatever they ask.The spaceThey can live the way they live in there home no formalityGuest accessthey can go and use whatever they want no restrictions, they are our guest we would do our best to accommodate everything they wantOther things to noteIf you give smile you get back smile, give respect and take respect back 😃
Facilities: Entire house, Sleeps 2, 1 bedroom, 1 bathroom, 1 bed, 516 sq m, Kitchen, Pet-friendly, Smoke-free, Free parking, Paid Wi-Fi
Images: https://lh3.googleusercontent.com/proxy/pa4IU8giwhthREwXxNpPotPFb0AwT-6oc8AtVdJyeyTspueKws4ZiAyLN5

Name: Al-Noor Hotel
Inserted data for hotel: Al-Noor Hotel
Stored data for hotel: Al-Noor Hotel
Address: 6G65+5VX, Mohalla Qaisarabad, Multan, Punjab
Price: Rs 10,596
Total Reviews: 177 reviews
Average Review: 3.8
About: Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeRestaurant, InternetWi-FifreeServicesFront desk24-hourFull-service laundryParking & transportParkingfreeTransferLocal shuttleFood and drinkRestaurantRoom serviceBreakfastfreePoolsNo poolsNo hot tubWellnessNo fitness centreNo spa
Images: https://lh5.googleusercontent.com/p/AF1QipN3xa3FbFalPXBFQ31CW-h8Kg6oBatbe5chtTZe=w252-h447-k-no, //lh6.googleusercontent.com/proxy/ld8aUTrrJmt51tpEz9t-IK1baHb2LAJTOlidlcqMQH-vG8aRwBSTV2k6Vhmp9mpPdTQBEHfvNUwlBWArsPtku35mjMS46M-C_S5YXdjdb3YAMFGKCZwFbeY-FTDmzDPnZIPQHEbciPzUSJRKmry9SzpsuF8JDXY=w252-h189-k-no, //lh3.googleusercontent.com/proxy/84wuFcgOZqMKeLyG3y8fmveXJsMNMP6VgrDSqrkLsIPAnbmmAv_wpKRKr7aOhuQtl_v7SRBD92rDWNCm0NJJ5b8Hh7vEvID5UJauYkiRV81aTTLmWMB-AXrrkuEOHlWqefdV0f

Name: Hotel Palace Inn
Price element not found.
About section not found.
Inserted data for hotel: Hotel Palace Inn
Stored data for hotel: Hotel Palace Inn
Address: Behind Cardiology Near Auto Plaza Dera Adda Multan Multan Punjab Region, 60000
Price: N/A
Total Reviews: 3 reviews
Average Review: 4.0
About: N/A
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipOJ7nYuFTTbk43hGQ86Hdr6X5sqYeA0IPd3c6QD=w252-h559-k-no, https://lh5.googleusercontent.com/p/AF1QipOJ7nYuFTTbk43hGQ86Hdr6X5sqYeA0IPd3c6QD=w252-h559-k-no
Reviews:
  Username: Technical Rafay
  Rating: 5/5
  Review: Nice hotel in Multan
  Username: Naseer Nasar
  Rating: 3/5
  Review: It was good
  Username: khalil ur Rehman
  Rating: 4/5
  Review: Rooms2.0Service4.0Location3.0Hotel highlightsQuietNoteworthy detailsTry to make more comfortable rooms ND availability of services .
https://www.google.com/travel/search?q=multan%20%20hotels&ts=CAESCgoCCAMKAggDEAAaTwoxEi8yJTB4MzkzYjMxNTc3OGRlYTdkOToweGJhZDcyZmM3NGU1NWQ0MmY6Bk11bH

...

Name: Luxury House in Wapda Town, Multan
address not avalible
Inserted data for hotel: Luxury House in Wapda Town, Multan
Stored data for hotel: Luxury House in Wapda Town, Multan
Address: no address
Price: Rs 21,704
Total Reviews: Rs 21,704 total1 night with taxes + fees
Average Review: 1.0
About: DetailsDishes and dining utensils,Kitchen basics (cookware, oils, condiments),Refrigerator,Balcony or terrace,TV,Wi-Fi,Air conditioning,Heater,Private entrance,Coffee or tea,Kitchen,Hair dryer,Toiletries,Towels,Free parking,Desk/workspace,Closet,Iron,Washer,Smoking allowed,Website
Facilities: Sleeps 2, 1 bedroom, 1 bathroom, 1 bed, Air conditioning, Balcony, Ironing board, Kitchen, Cable TV, Washing machine, Free parking, Free Wi-Fi
Images: https://lh6.googleusercontent.com/proxy/W8XyJA6iOo3tJa3PjrXs5nsj-osw3V2hqDaN5SOOlAUbr9JR5MxuPUiIieSOYKJXKVCWHR1JfkJAhHfZmIwhYwUogddbOCshfu3Kyy7e11r3kK-bAB69zj0xsql1q8TwWKiA7XbU_iMsepEs5ghLZSR-BTKRSL0=s287-w287-h192-n-k-no-v1, https://lh3.googleusercontent

Name: Ramada by Wyndham Multan
Inserted data for hotel: Ramada by Wyndham Multan
Stored data for hotel: Ramada by Wyndham Multan
Address: •
Price: Rs 25,514
Total Reviews: 7,123 reviews
Average Review: 4.4
About: This traditional hotel is 2.2 km from Tomb of Shah Rukn-e-Alam, 2.6 km from Ibn-e-Qasim Bagh Stadium and 7.1 km from Jinnah Park.… MoreStraightforward rooms and suites come with high-speed Internet and flat-screen TVs. Some offer whirlpool tubs, minifridges and/or sitting areas. Kids age 17 and under stay free.A continental breakfast buffet is complimentary. There’s also an all-day buffet restaurant, plus a cafe and a Chinese restaurant. Other amenities include an outdoor pool and an exercise room.Check-in time: 14:00Check-out time: 12:00
Facilities: PoolParkingfreeBreakfastfreeWi-Fifree, InternetWi-FifreeWi-Fi in public areasPublic Internet workstationPolicies & paymentsSmoke-free propertyCredit cardsDebit cardsCashChequesChildrenChild-friendlyPoolsOutdoor poolAdult-only pool

Name: MULTAN SWISS HOTEL
Inserted data for hotel: MULTAN SWISS HOTEL
Stored data for hotel: MULTAN SWISS HOTEL
Address: Northern Bypass, Gillani St, near Haider arcade, Multan, 60000
Price: Rs 6,749
Total Reviews: 54 reviews
Average Review: 4.8
About: Check-out time: 12:00
Facilities: ParkingfreeWi-FifreeAir conditioningBreakfastextra charge, InternetWi-FifreePolicies & paymentsSmoke-free propertyCredit cardsDebit cardsCashChequesPoolsNo poolsHot tubParking & transportParkingfreeAirport shuttleextra chargeLocal shuttleAccessibilityAccessibleAccessible parkingPetsPet-friendlyfreeRoomsAir conditioningKitchen in some roomsRefrigerator in some roomsMicrowave in some roomsFood and drinkRoom serviceBreakfastextra chargeActivitiesBicycle hireextra chargeServicesFront desk24-hourBaggage storageConciergeGrocery shopFull-service laundryWake up callsHousekeepingdailyWellnessNo fitness centreNo spaDoctor on callBusiness & eventsBusiness centreMeeting roomsLanguages spokenEnglishHindiBathroomsPriva

Name: Hotel One Tariq Road Multan
Inserted data for hotel: Hotel One Tariq Road Multan
Stored data for hotel: Hotel One Tariq Road Multan
Address: •
Price: Rs 23,278
Total Reviews: 2,292 reviews
Average Review: 4.4
About: Set 7 minutes on foot from shopping at the United Mall, this straightforward hotel is 3 km from the Tomb of Shah Rukn-e-Alam and 5 km from Multan International Airport.… MoreUnderstated rooms feature flat-screen TVs, minifridges, and tea and coffeemaking equipment, as well as sitting areas and en suite bathrooms.Parking and a breakfast buffet are complimentary. Other amenities include an outdoor pool, a fitness centre and meeting facilities.Check-in time: 12:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeAir conditioning, InternetWi-FifreeServicesFront desk24-hourFull-service laundryPoolsNo poolsNo hot tubWellnessNo spaAccessibilityAccessibleRoomsAir conditioningFood and drinkRestaurantRoom serviceBreakfastfreeBreakfast buffetChildrenChild-friend

Name: Hotel DE Shalimar - Multan
Inserted data for hotel: Hotel DE Shalimar - Multan
Stored data for hotel: Hotel DE Shalimar - Multan
Address: •
Price: Rs 7,916
Total Reviews: 1,680 reviews
Average Review: 4.1
About: Check-in time: 14:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeAir conditioning, InternetWi-FifreeWi-Fi in public areasPolicies & paymentsSmoke-free propertyCredit cardsDebit cardsCashChildrenChild-friendlyPoolsNo poolsNo hot tubParking & transportParkingfreeSelf parkingfreeAirport shuttleextra chargePrivate car serviceextra chargeAccessibilityAccessibleAccessible parkingLanguages spokenArabicEnglishHindiBathroomsBathtub in some roomsShowerFood and drinkRestaurantTable serviceRoom serviceBreakfastfreeBreakfast buffetServicesFront desk24-hourBaggage storageConciergeGrocery shopCurrency exchangeFull-service laundryWake up callsHousekeepingdailyTurndown serviceWellnessNo fitness centreNo spaDoctor on callBusiness & eventsMeeting roomsPetsNo petsRoomsA

In [28]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name = soup.find('h1', class_='FNkAEc o4k8l')
        if name:
            hotel_name = name.text.strip()
            print("Name:", hotel_name)
            hotel_data['name'] = hotel_name
        else:
            print("Hotel name not found.")
            hotel_data['name'] = None 
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Abbottabad '
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

               

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        
        

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=abbottabad%20hotels&ts=CAESCgoCCAMKAggDEAAaUwo1EjMyJTB4MzhkZTMxMTE1NTdhYzUxNzoweDZlNTlhNjM1YjEyZTk1MmM6CkFiYm90dGFiYWQSGhIUCgcI6A8QCBgBEgcI6A8QCBgCGAEyAhAAKgcKBToDUEtS&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgmDgrWPFRE-QBGrbcMIts9RQBISCQej9sOcXz5AEattw0ha61FAMAG6AQdyZXZpZXdz&qs=CAESBENLSUIgASgAOA1IAA&ved=0CAAQ5JsGahgKEwjI3LKi-LKHAxUAAAAAHQAAAAAQ0QE')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1
max_hotels = 200

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    if len(all_links) >= max_hotels:
        all_links = all_links[:max_hotels]  # Limit the total links to max_hotels
        break
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '/html/body/c-wiz[2]/div/c-wiz/div[1]/div[1]/div[2]/div[2]/main/c-wiz/span/c-wiz/c-wiz[23]/div[1]/button[1]/span')
        print("Found next page button.")
    except NoSuchElementException:
        
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[25]/div[1]/button[1]/span')
         #   print("Found alternate next page button.")
        except NoSuchElementException:
         #   # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'new_db' exists.
Collection 'hotel_data' exists in database 'new_db'.
Database 'new_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 18 links from page 1.
Found next page button.
Scraping page 2...
Collected 20 links from page 2.
Scraping page 3...
Collected 20 links from page 3.
Scraping page 4...
Collected 20 links from page 4.
Scraping page 5...
Collected 20 links from page 5.
Scraping page 6...
Collected 20 links from page 6.
Scraping page 7...
Collected 20 links from page 7.
Scraping page 8...
Collected 20 links from page 8.
Scraping page 9...
Collected 20 links from page 9.
Scraping page 10...
Collected 20 links from page 10.
Scraping page 11...
Collected 20 links from page 11.
All Scraped data from links:
1
Name: Hill Top Villa - Villa with Garden View
address not avalible
Price element not found.
Inserted data for hotel: Hill Top Villa - Villa with Garden View
Stored data for hotel: Hill Top Villa - Villa with Garden View
Address: no addr

Name: Hill Top Villa - Superior Villa
address not avalible
Price element not found.
Inserted data for hotel: Hill Top Villa - Superior Villa
Stored data for hotel: Hill Top Villa - Superior Villa
Address: no address
Price: N/A
Total Reviews: 4–7 Aug
Average Review: CloseView list
About: DetailsHill Top Villa is a sustainable villa in Nathia Gali, where guests can make the most of its garden and shared lounge. This property offers access to a terrace, free private parking and free WiFi. Guests will have a special experience as the villa offers a fireplace. Featuring a private entrance, this villa consists of 1 living room, 3 separate bedrooms and 3 bathrooms with a bath and a shower. Boasting a terrace with garden views, this villa also provides a washing machine and a flat-screen TV with cable channels. The unit offers 6 beds.Website
Facilities: Entire villa, Sleeps 10, 3 bedrooms, 3 bathrooms, 6 beds, Air conditioning, Airport shuttle, Balcony, Child-friendly, Cot, Fireplace, Fitness 

Name: Republika by Summit Resorts - Two-Bedroom Suite
address not avalible
Price element not found.
Inserted data for hotel: Republika by Summit Resorts - Two-Bedroom Suite
Stored data for hotel: Republika by Summit Resorts - Two-Bedroom Suite
Address: no address
Price: N/A
Total Reviews: 10–11 Aug
Average Review: CloseView list
About: DetailsLocated in Abbottābād in the Federally Administered Tribal Area region, Republika by Summit Resorts features a garden. This property offers access to a terrace, free private parking and free WiFi. The fireplace is a top feature of this suite. This spacious suite comes with 1 living room, 2 separate bedrooms and 2 bathrooms with a bath and free toiletries. Guests will find kitchenware and a microwave in the kitchenette. The suite also includes a barbecue. This air-conditioned suite consists of a dining area, a flat-screen TV with cable channels a private entrance and a terrace. The unit has 3 beds.Website
Facilities: Entire house, Sleeps 4, 2 bedro

Name: Gali's End By Roomy, Kalabagh Nathiagali - Superior Apartment
address not avalible
Price element not found.
Inserted data for hotel: Gali's End By Roomy, Kalabagh Nathiagali - Superior Apartment
Stored data for hotel: Gali's End By Roomy, Kalabagh Nathiagali - Superior Apartment
Address: no address
Price: N/A
Total Reviews: 4–7 Aug
Average Review: CloseView list
About: DetailsGali's End By Roomy, Kalabagh Nathiagali is situated in Nathia Gali and offers a terrace. This apartment features free private parking and a 24-hour front desk. Boasting family rooms, this property also provides guests with an outdoor fireplace. This spacious apartment consists of 1 living room, 4 separate bedrooms and 3 bathrooms with a shower and free toiletries. Guests can make meals in the fully equipped kitchen that features a stovetop, an oven and an electric kettle. Featuring a terrace with garden views, this apartment also provides a private entrance and a flat-screen TV. The unit offers 4 beds.Websi

Name: Gali's End By Roomy, Kalabagh Nathiagali - Two-Bedroom Apartment
address not avalible
Price element not found.
Inserted data for hotel: Gali's End By Roomy, Kalabagh Nathiagali - Two-Bedroom Apartment
Stored data for hotel: Gali's End By Roomy, Kalabagh Nathiagali - Two-Bedroom Apartment
Address: no address
Price: N/A
Total Reviews: 4–7 Aug
Average Review: CloseView list
About: DetailsGali's End By Roomy, Kalabagh Nathiagali is situated in Nathia Gali and offers a terrace. This apartment features free private parking and a 24-hour front desk. Boasting family rooms, this property also provides guests with an outdoor fireplace. Boasting a private entrance, this apartment features 1 living room, 2 separate bedrooms and 2 bathrooms with a shower and slippers. Guests can make meals in the fully equipped kitchen that has a stovetop, an oven and an electric kettle. Featuring a terrace with garden views, this apartment also features soundproof walls and a flat-screen TV. The unit has 3 b

...

Name: A.W.K Hotels
Inserted data for hotel: A.W.K Hotels
Stored data for hotel: A.W.K Hotels
Address: Jadoon Plaza Phase 2 Rd, opposite limelight, Jinnahabad Abbottabad, Khyber Pakhtunkhwa 32154
Price: Rs 3,200
Total Reviews: 53 reviews
Average Review: 4.3
About: InternetWi-FifreeServicesFront desk24-hourFull-service laundryWellnessNo fitness centreNo spa
Facilities: BreakfastfreeWi-Fifree, InternetWi-FifreeServicesFront desk24-hourFull-service laundryWellnessNo fitness centreNo spaFood and drinkRoom serviceBreakfastfreePoolsNo poolsNo hot tub
Images: https://lh5.googleusercontent.com/p/AF1QipPGKKPYgXJPVewTPrsGaUNBrVfiP6UuR3Nrxbxe=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipOPr2kv19opL_-I-U5pJKcRYeToYhq1SiaP-y9R=w252-h180-k-no, https://lh5.googleusercontent.com/p/AF1QipOR6z6D6wovvHXgO7Bb9u9Y-vJyUi9YkDeRQbNc=w252-h189-k-no
Reviews:
  Username: abdullah khan
  Rating: 5/5
  Review: A.W.K Hotels provide an exceptional stay experience. From luxurious accommodations to impecca

Name: Usmania guest house
Inserted data for hotel: Usmania guest house
Stored data for hotel: Usmania guest house
Address: Shahzaman town, Jhangi Rd, Amir Alam Awan Town, Abbottabad, Khyber Pakhtunkhwa 22050
Price: Rs 4,050
Total Reviews: 125 reviews
Average Review: 3.9
About: Check-in time: 13:00Check-out time: 13:00
Facilities: ParkingfreeBreakfastfreeAir conditioningWi-Fi, InternetWi-FiServicesFront desk24-hourFull-service laundryParking & transportParkingfreeTransferPetsNo petsFood and drinkRoom serviceBreakfastfreePoolsNo poolsNo hot tubWellnessNo fitness centreNo spaRoomsAir conditioning
Images: //lh5.googleusercontent.com/proxy/wEeL3p4frigChEW3ZpM349PUQMZUvCukgo2vlvDq8EwDCnpdAykoePzBr2pvHFfBNCJ4RRy7yMpoxvGnLWSlhMliAnsToLiQGcPDfxtwp4kGY70rfCoC0me9b5FZADizckALA4JnuZGVZ2IepbA1wPhR-0UIgA=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipNI-0S11zPUoO_C_Jms1YdqhOeN7MnZob6kBaUH=w252-h336-k-no, //lh5.googleusercontent.com/proxy/00CFlwBNlCfmdnV0o_r9CyeSgqGrsD5s-oN3CbRhrrRxgNTBAwj

Name: The Point by Roomy, Thandiani
Price element not found.
Hotel The Point by Roomy, Thandiani already exists in the database. Skipping insertion.
Stored data for hotel: The Point by Roomy, Thandiani
Address: Gali Banian, Thandiani Road, Thandiani, Abbottabad, Khyber Pakhtunkhwa
Price: N/A
Total Reviews: 277 reviews
Average Review: 4.4
About: Check-in time: 14:00
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipNK7bDwKbWdiHVrPPxLbctN6VgXldkgrcK_Jyvp=w252-h168-k-no, https://lh5.googleusercontent.com/p/AF1QipMA1-Jau4OBr-SMtkfdD1wQv2F9a-M3TRhVKi1H=w252-h187-k-no, https://lh5.googleusercontent.com/p/AF1QipOdTTZrOAfzT1rBjmVRqhOntNvbimlBV5C6Ge3p=w252-h168-k-no
Reviews:
  Username: Salman Imtiaz
  Rating: 5/5
  Review: From check-in to check out, the service and courtesy provided by the staff were excellent, especially since Mustansar always went a step ahead to ensure all needs were met. The support staff all of them were extra helpful. Downsides include the approach road  no

Price element not found.
Inserted data for hotel: Alpine Hotel & Resort
Stored data for hotel: Alpine Hotel & Resort
Address: Alpine Hotel, Road, Nathia Gali, Abbottabad, Khyber Pakhtunkhwa
Price: N/A
Total Reviews: 3,213 reviews
Average Review: 4.3
About: Offering views of the Miranjani Peak, this unassuming hotel along Green Spot Road is 3 km from the Lalazar Wildlife Park. It's 4 km from hiking at Mukshpuri Peak.… MoreThe laid-back rooms offer free Wi-Fi, flat-screen TVs, and terraces with mountain views. Upgraded rooms add sitting areas. There are 2 separate houses featuring 3-or-4 bedrooms, plus living areas, kitchens and patios.Amenities include a warm lounge and an airy restaurant. Parking is available.Check-in time: 15:00Check-out time: 12:00
Facilities: ParkingfreeWi-FifreeBreakfastextra chargeRestaurant, InternetWi-FifreeServicesFront desk24-hourFull-service laundryPoolsNo poolsNo hot tubWellnessNo fitness centreNo spaPetsNo petsFood and drinkRestaurantRoom serviceBreakfastex

Name: Alaf Laila Guest House Abbottabad
Hotel Alaf Laila Guest House Abbottabad already exists in the database. Skipping insertion.
Stored data for hotel: Alaf Laila Guest House Abbottabad
Address: •
Price: Rs 8,000
Total Reviews: 627 reviews
Average Review: 4.1
About: Check-in time: 11:30Check-out time: 13:00
Facilities: ParkingfreeWi-FifreeAir conditioningRestaurant, InternetWi-FifreeWi-Fi in public areasPublic Internet workstationPolicies & paymentsCashChildrenChild-friendlyBabysittingActivities for kidsParking & transportParkingfreePetsNo petsLanguages spokenEnglishFood and drinkRestaurantTable serviceRoom serviceNo breakfastServicesFront desk24-hourFull-service laundryHousekeepingdailyPoolsNo poolsNo hot tubWellnessNo fitness centreNo spaRoomsAir conditioning
Images: //lh6.googleusercontent.com/proxy/mJa0xWBguJaybPRlcSWd4nEacB1I__DHkHc4K0ezc1j8AEpRU7rWaTIQRJ8PLfgtq_lAWCDPScSseVfH5ZNCq7j_mNUyEXBSLWAjcec4jPD207maAk9zGs6v3vtMeBseLqvel1P-Md4GeDtm4WgJ_zhDlll22i8=w252-h167-k-no, https:/

In [3]:
from pymongo import MongoClient
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from time import sleep
from urllib.parse import urljoin
import pandas as pd


def scrape_page(url, browser,collection,hotel_df):
    hotel_data = {}
    try:
        browser.get(url)
        sleep(5)
        # Wait for the hotel name to be visible and extract it
        #hotel_name = WebDriverWait(browser, 10).until(
        #    EC.visibility_of_element_located((By.XPATH, '//h1[@class="e1f7icnh1"]'))
       # ).text
    
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        sleep(4)
        # Extract and print the name and price
        name = soup.find('h1', class_='FNkAEc o4k8l')
        if name:
            hotel_name = name.text.strip()
            print("Name:", hotel_name)
            hotel_data['name'] = hotel_name
        else:
            print("Hotel name not found.")
            hotel_data['name'] = None 
        address=soup.find('span',class_='CFH2De')
        if address:
            add=address.text.strip()
            
            hotel_data['address'] = add
        else:   
            hotel_data['address'] = "no address"
            print("address not avalible")
         # Extract images
        #images = browser.find_elements(By.XPATH, '//img[@class="R1Ybne nDgy9d"]')
        images_container = soup.find('div', class_='NBZP0e xbmkib')
        if images_container:
            images = images_container.find_all('img', class_='x7VXS wnGtLb q5P4L')
            hotel_data['images'] = []
    
            for img in images[:3]:
                img_src = img.get('src')
                if img_src:
                    hotel_data['images'].append(img_src)
                    
                else:
                    print("Image source not found.")
        else:
            print("Images container not found.") 

        xpath = '//*[@id="prices"]'
        element = browser.find_element("xpath", xpath)
        element.click()
        price_element = soup.find('span', class_='MW1oTb')
        if price_element:
            price = price_element.text.strip()
            
            hotel_data['price'] = price
        else:
            print("Price element not found.")
       
        hotel_data['city']='Batakundi '
        #hotel_data['total_reviews'] = browser.find_element(By.XPATH, '//span[@class="hfpxzc"]').text
        #hotel_data['average_review'] = browser.find_element(By.XPATH, '//div[@class="e10twf7w5"]/span').text
        #hotel_data['about'] = browser.find_element(By.XPATH, '//div[@class="nDgy9d"]').text

       # for facs in fac:
        #    print("Facilities",facs.text.strip())
       # hotel_data['facilities'] = [facility.text for facility in facilities]
        xpath = '//*[@id="details"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        facilities=soup.find_all('div',class_='xGm0S B8PKdc XSe9p')
        hotel_data['facilities']=[] 
        for facility in facilities:
            fac=facility.text.strip()
            hotel_data['facilities'].append(fac) 
            
            
            
        about=soup.find('section',class_='O3oTUb')
        if about:
            about=about.text.strip()    
            
            hotel_data['about'] = about
        else :
            try:
                about1 = soup.find('div', class_='U1L8Pd')
                if about1:
                    about1 = about1.text.strip()
                    
                    hotel_data['about'] = about1
                else:
                    print("About section not found.")
                    hotel_data['about'] = "N/A"

            except AttributeError as e:
                print(f"Error extracting about section: {e}")
                hotel_data['about'] = "N/A"
            try:
                # Find facilities using different classes and merge results
                facilities = soup.find_all('ul', class_='ezpVOe') + soup.find_all('div', class_='eFfcqe G8T82')
    
                hotel_data['facilities'] = []
    
                for facility in facilities:
                    fac = facility.text.strip()
                    hotel_data['facilities'].append(fac)
                    

            except AttributeError as e:
                print(f"Error extracting facilities: {e}")
                hotel_data['facilities'] = []

                
       
        # Extract reviews
        # Print the current URL for verification
        xpath = '//*[@id="reviews"]/span'
        element = driver.find_element("xpath", xpath)
        element.click()
        overall_rating=soup.find('div',class_='FBsWCd')
        overallrating=soup.find('div',class_='BARtsb')
        overall=soup.find('span',class_='QB2Jof')
        if overall_rating:
            overall_rating=overall_rating.text.strip()    
            
            hotel_data['average_review'] =overall_rating
        elif overallrating:
            overallrating=overallrating.text.strip()    
            
            hotel_data['average_review'] = overallrating
        elif overall:
            overall=overall.text.strip()    
            
            hotel_data['average_review'] = overall
        else:
            hotel_data['average_review'] = 0
        
        total_rating=soup.find('span',class_='P2NYOe GFm7je sSHqwe')
        total=soup.find('div',class_='sSHqwe')
        totalr=soup.find('span',class_='CQYfx')
        if total_rating:
            total_rating=total_rating.text.strip()
            
            hotel_data['total_reviews'] =total_rating
        elif total:
            total=total.text.strip()    
            
            hotel_data['total_reviews'] = total
        elif totalr:
            totalr=totalr.text.strip()    
            
            hotel_data['total_reviews'] = totalr
        else: 
            print("total people rated 0")
            hotel_data['total_reviews'] = 0
        reviews = []
    
        try:
            usernames = soup.find_all('a', class_='DHIhE QB2Jof')
            ratings = soup.find_all('div', class_='GDWaad')
            review_texts = soup.find_all('div', class_='STQFb eoY5cb')

            for username, rating, review_text in zip(usernames, ratings, review_texts):
                username_text = username.text.strip()
                rating_text = rating.text.strip()
                review_text = review_text.text.strip()

               

                reviews.append({'username': username_text, 'rating': rating_text, 'review_text': review_text})

        except NoSuchElementException:
            print("ERROR")

        except NoSuchElementException:
            print("Error: Element not found.")

        hotel_data['reviews'] = reviews


        # Append data to the DataFrame
       # hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        hotel_df = pd.concat([hotel_df, pd.DataFrame([hotel_data])], ignore_index=True)
        

        
        # Remove duplicates based on 'name' column
        hotel_df.drop_duplicates(subset=['name'], inplace=True)

        
        

        # Insert non-duplicate data into MongoDB
        for index, row in hotel_df.iterrows():
            hotel_name = row['name']
            # Check if the hotel already exists in the collection
            if collection.find_one({'name': hotel_name}) is None:
                collection.insert_one(row.to_dict())
                print(f"Inserted data for hotel: {hotel_name}")
            else:
                print(f"Hotel {hotel_name} already exists in the database. Skipping insertion.")                          
                # Print the scraped data
        print(f"Stored data for hotel: {hotel_name}")
        print(f"Address: {hotel_data.get('address', 'N/A')}")
        print(f"Price: {hotel_data.get('price', 'N/A')}")
        print(f"Total Reviews: {hotel_data.get('total_reviews', 'N/A')}")
        print(f"Average Review: {hotel_data.get('average_review', 'N/A')}")
        print(f"About: {hotel_data.get('about', 'N/A')}")
        print(f"Facilities: {', '.join(hotel_data.get('facilities', []))}")
        print(f"Images: {', '.join(hotel_data.get('images', []))}")
        print("Reviews:")
        for review in hotel_data['reviews']:
            print(f"  Username: {review['username']}")
            print(f"  Rating: {review['rating']}")
            print(f"  Review: {review['review_text']}")
    
    except (NoSuchElementException, TimeoutException) as e:
        print(f"Error extracting data from {link}: {e}")

# MongoDB setup
client = MongoClient('mongodb://localhost:27017/')  # Update with your MongoDB connection string

# Database and collection names
db_name = 'new_db'
collection_name = 'hotel_data'

# Check if the database exists
if db_name in client.list_database_names():
    print(f"Database '{db_name}' exists.")
else:
    print(f"Database '{db_name}' does not exist. Creating database '{db_name}'.")

# Connect to the database
db = client[db_name]

# Check if the collection exists
if collection_name in db.list_collection_names():
    print(f"Collection '{collection_name}' exists in database '{db_name}'.")
else:
    print(f"Collection '{collection_name}' does not exist in database '{db_name}'. Creating collection '{collection_name}'.")

# Connect to the collection
collection = db[collection_name]

# Confirmation message
print(f"Database '{db_name}' and collection '{collection_name}' are ready for use.")
# Initialize the browser


# Create a DataFrame to store the hotel data
hotel_df = pd.DataFrame(columns=[
    'name', 'address', 'price', 'total_reviews', 'average_review', 'about','city','facilities', 'images', 'reviews'
])
                                   
# Initialize the browser
driver = webdriver.Chrome()
driver.get('https://www.google.com/travel/search?q=batakundi%20hotels&ts=CAESCgoCCAMKAggDEAAaUgo0EjIyJTB4MzhlNzQ5MTM4MDU0NmYzNzoweGZjNzdkYTgyNTM2YmVjYmI6CUJhdGFrdW5kaRIaEhQKBwjoDxAIGAESBwjoDxAIGAIYATICEAAqBwoFOgNQS1I&ictx=3&hl=en-PK&gl=pk&g2lb=4814050%2C4874190%2C4893075%2C4965990%2C10210221%2C72277293%2C72302247%2C72317059%2C72406588%2C72414906%2C72421566%2C72462234%2C72470899%2C72471280%2C72472051%2C72473841%2C72481459%2C72485658%2C72486593%2C72494250%2C72499705%2C72513513%2C72536387%2C72549171%2C72569093%2C72570850%2C72602734%2C72605013%2C72606237%2C72608658%2C72616120%2C72619927%2C72620306%2C72620956%2C72624691%2C72632490%2C72632491%2C72634630%2C72640791%2C72648289%2C72653660%2C72658032&ap=KigKEgmmR5jGgPJAQBET_G_lljdSQBISCd8r01WtPUFAERP8b2XfblJAMAG6AQdyZXZpZXdz&qs=CAASBENLSUIgACgAOA1IAA&ved=0CAAQ5JsGahgKEwjIkvy017OHAxUAAAAAHQAAAAAQqAI')
driver.maximize_window()

# Allow some time for the page to load
sleep(5)

all_links = []
page_number = 1
max_hotels = 180

while True:
    print(f"Scraping page {page_number}...")

    # Parse the page source
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Find all 'a' tags with class 'PVOOXe' and extract 'href' attributes
    links = [a['href'] for a in soup.find_all('a', class_='PVOOXe') if 'href' in a.attrs]

    # Validate and format links
    base_url = 'https://www.google.com'
    valid_links = [urljoin(base_url, link) for link in links]
    all_links.extend(valid_links)

    print(f"Collected {len(valid_links)} links from page {page_number}.")

    # Break the loop if the total number of collected links reaches or exceeds max_hotels
    if len(all_links) >= max_hotels:
        all_links = all_links[:max_hotels]  # Limit the total links to max_hotels
        break
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(2)
    try:
        # Try to find the next page button
        next_button = driver.find_element(By.XPATH, '//*[@id="id"]/c-wiz/c-wiz[16]/div[1]/button/span')
        print("Found next page button.")
    except NoSuchElementException:
        
        try:
            # Try the alternate next page button
            next_button = driver.find_element(By.XPATH, '/html/body/c-wiz[2]/div/c-wiz/div[1]/div[1]/div[2]/div[2]/main/c-wiz/span/c-wiz/c-wiz[23]/div[1]/button[1]/span')
         #   print("Found alternate next page button.")
        except NoSuchElementException:
         #   # If no next button is found, break the loop
            print("No more pages found. Stopping the scraping process.")
            break

    # Click the next button
    next_button.click()

    # Allow some time for the next page to load
    sleep(5)
    page_number += 1

number=1
# Print all the collected links
print("All Scraped data from links:")
for link in all_links:
    print(number)
    scrape_page(link,driver,collection,hotel_df)
    print(link)
    number+=1
    

    
print("Scraping and data storage complete.")


Database 'new_db' exists.
Collection 'hotel_data' exists in database 'new_db'.
Database 'new_db' and collection 'hotel_data' are ready for use.
Scraping page 1...
Collected 11 links from page 1.
Found next page button.
Scraping page 2...
Collected 18 links from page 2.
Scraping page 3...
Collected 18 links from page 3.
Scraping page 4...
Collected 18 links from page 4.
Scraping page 5...
Collected 18 links from page 5.
Scraping page 6...
Collected 18 links from page 6.
Scraping page 7...
Collected 19 links from page 7.
No more pages found. Stopping the scraping process.
All Scraped data from links:
1
Name: LEGEND HOTEL NARAN
About section not found.
Inserted data for hotel: LEGEND HOTEL NARAN
Stored data for hotel: LEGEND HOTEL NARAN
Address: WJ2X+FRV, Bypass Road،, Naran, Mansehra, Khyber Pakhtunkhwa
Price: Rs 23,151
Total Reviews: 17 reviews
Average Review: 4.2
About: N/A
Facilities: 
Images: //lh3.googleusercontent.com/proxy/tY4xoyhOipOn9bSRmJmGzVYh8HXVhoh6Kk7ii_nLkZAhiN0Grd5JQoxoHp

Name: Frontier Hotel
Price element not found.
Hotel Frontier Hotel already exists in the database. Skipping insertion.
Stored data for hotel: Frontier Hotel
Address: N15, Main Bazar, Naran, Khyber Pakhtoonkhwa, 21300
Price: N/A
Total Reviews: 4 reviews
Average Review: 3.8
About: Check-out time: 12:00
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipN4_l0N2RGO1d-iyiW4QkQRPm4VOzDHRsT7j-0=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipN4_l0N2RGO1d-iyiW4QkQRPm4VOzDHRsT7j-0=w252-h189-k-no, https://lh5.googleusercontent.com/p/AF1QipNyWj-nmH7cRFvwI0yqwiKY0tdO8kmo-xWp9pM=w252-h189-k-no
Reviews:
  Username: Maqbool ur Rehman
  Rating: 3/5
  Review: Ok stay in
  Username: Arslan Mushtaq
  Rating: 5/5
  Review: Expensive
  Username: Imran Raheel
  Rating: 5/5
  Review: 
  Username: muneer wazir
  Rating: 2/5
  Review: 
https://www.google.com/travel/search?q=batakundi%20hotels&ts=CAESCgoCCAMKAggDEAAaUgo0EjIyJTB4MzhlNzQ5MTM4MDU0NmYzNzoweGZjNzdkYTgyNTM2YmVjYmI6CUJhdGFrdW5kaR

Name: Punjab foods
Price element not found.
About section not found.
Inserted data for hotel: Punjab foods
Stored data for hotel: Punjab foods
Address: WM52+P73, Naran, Mansehra, Khyber Pakhtunkhwa
Price: N/A
Total Reviews: 5 reviews
Average Review: 3.4
About: N/A
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipNpYAQPYCYqp29KPx2p4zxhVnwXjQdsvwo1ofbi=w252-h559-k-no, https://lh5.googleusercontent.com/p/AF1QipNpYAQPYCYqp29KPx2p4zxhVnwXjQdsvwo1ofbi=w252-h559-k-no, https://lh5.googleusercontent.com/p/AF1QipMAFyALPyS_Apm4r7Nr5UNalOLJNO5t69QT-q7F=w252-h559-k-no
Reviews:
  Username: Muhammad Ali Q
  Rating: 4/5
  Review: On the top of Naran Valley is this Punjab Hotel / Restaurant. Good bbq and freshly cooked items. Afghani Pulav is the best thing you could get your hands into. The steamed cooked rice in a stew of veg's n nuts mixed it is a tangible experience. The Kawaa or the green tea is icing on the cake.
  Username: vivek y
  Rating: 5/5
  Review: Punjab Hotel is was my fir

Name: Nine Tree Hotel Naran
Inserted data for hotel: Nine Tree Hotel Naran
Stored data for hotel: Nine Tree Hotel Naran
Address: WM56+WC, Jheel Road, Katha, Naran, Mansehra, Khyber Pakhtunkhwa 54000
Price: Rs 25,381
Total Reviews: 23 reviews
Average Review: 4.7
About: Check-in time: 14:00
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipO0viSPIre5fqhUF8MzBtz-6l6E3dXnSVAAjqRJ=w252-h252-k-no, https://lh5.googleusercontent.com/p/AF1QipPuPm-jWiMSP6oeBR0wN-wr3-b3POK6NoLTIA-a=w252-h186-k-no, https://lh5.googleusercontent.com/p/AF1QipN6UCS33mjbEvdizsyDyVJ3TjpjyURlOkYlFpqu=w252-h189-k-no
Reviews:
  Username: Kashif Majeed
  Rating: 5/5
  Review: This hotel exceeded my expectations. Well-trained staff that are caring and make yourself feel like at home. I enquired, by the way, about whole wheat roti and to my surprise I had it the next day. I have to set off after Fajar prayers. When I approached for check out at 5:00 a.m. on 27th of July they asked me to give them some time to pr

Name: Belmont Naran
Inserted data for hotel: Belmont Naran
Stored data for hotel: Belmont Naran
Address: Saiful Muluk Rd, Katha, Naran, Mansehra, Khyber Pakhtunkhwa 21200
Price: Rs 17,472
Total Reviews: 59 reviews
Average Review: 4.5
About: Check-in time: 12:00Check-out time: 11:30
Facilities: ParkingfreeBreakfastfreeWi-FifreeRestaurant, InternetWi-FifreePolicies & paymentsCredit cardsDebit cardsCashChildrenChild-friendlyParking & transportParkingfreeSelf parkingfreeBusiness & eventsMeeting roomsPetsPet-friendlyFood and drinkRestaurantTable serviceRoom service24-hourBreakfastfreeServicesFront desk24-hourFull-service laundryPoolsNo poolsNo hot tubWellnessNo fitness centreNo spaBathroomsPrivate bathroomShower
Images: https://lh5.googleusercontent.com/p/AF1QipNY4AewCXO4hWjnM5nOHsU_UETyoVszaVBM2tIi=w252-h189-k-no, //lh3.googleusercontent.com/proxy/tJGwn1qcKbTU7a1l-XjT_z8kgFqZDKgQifaeWcFFPUz1LZ9Sv6dmc870Urjyvab26gKLyWH-CUPdv7yiSoztJNG4_t3LWz9EC8IW87kwjgX0JRNUHB0SXA4eSMzszVASl-P8S2R53FoorLsk

...

Name: Hotel Deep Forest
Price element not found.
Inserted data for hotel: Hotel Deep Forest
Stored data for hotel: Hotel Deep Forest
Address: WM57+3Q2, jheel road, Katha, Mansehra, Khyber Pakhtunkhwa
Price: N/A
Total Reviews: 31 reviews
Average Review: 3.7
About: Check-in time: 14:00Check-out time: 12:00
Facilities: ParkingfreeWi-Fifree, InternetWi-FifreeServicesFront desk24-hourFull-service laundryParking & transportParkingfreeFood and drinkRoom servicePoolsNo poolsNo hot tubWellnessNo fitness centreNo spa
Images: //lh4.googleusercontent.com/proxy/SByhui_kP-x4j6A5S02-MmkngTwrepal0aif2DufemOtqLXrvzkMa4CHoPmKLfQE9vrmKzUARdYhHcihkTaN_TJ4RxwA0_3t3mRxKRJ-MXpljdiFU8kxNTI2G-QkherscQ_10fq8K58T-WRzxm_Y0KUNTb6jGg=w252-h189-k-no, //lh4.googleusercontent.com/proxy/SByhui_kP-x4j6A5S02-MmkngTwrepal0aif2DufemOtqLXrvzkMa4CHoPmKLfQE9vrmKzUARdYhHcihkTaN_TJ4RxwA0_3t3mRxKRJ-MXpljdiFU8kxNTI2G-QkherscQ_10fq8K58T-WRzxm_Y0KUNTb6jGg=w252-h189-k-no, //lh5.googleusercontent.com/proxy/lRms5cXs5fakj3IDm5epgjiH7_g

Name: Sarbun Guest house
Price element not found.
About section not found.
Inserted data for hotel: Sarbun Guest house
Stored data for hotel: Sarbun Guest house
Address: WM52+4CR, Naran, Mansehra, Khyber Pakhtunkhwa
Price: N/A
Total Reviews: 7 reviews
Average Review: 4.4
About: N/A
Facilities: 
Images: https://lh5.googleusercontent.com/p/AF1QipMEz-hxmg4VVQg0hNnPpAA2Nhb1VTEp-hF-r82l=w252-h448-k-no, https://lh5.googleusercontent.com/p/AF1QipMEz-hxmg4VVQg0hNnPpAA2Nhb1VTEp-hF-r82l=w252-h448-k-no, https://lh5.googleusercontent.com/p/AF1QipOY6t0tF7PS4EauIHR0AsVdX_vuwnwhZ34hM_lN=w252-h189-k-no
Reviews:
  Username: Muhammad Usama
  Rating: 3/5
  Review: Average service with electricity and water availability problem
  Username: Sayyab Abbasi
  Rating: 5/5
  Review: Nice
  Username: Mani Butt
  Rating: 4/5
  Review: Gdd
  Username: Tehniyat Waqas
  Rating: 5/5
  Review: 
  Username: shujaat rahim
  Rating: 4/5
  Review: 
  Username: Ahmed Hasan
  Rating: 5/5
  Review: 
  Username: Ali Shan
  Ra

Name: HOTEL deMANCHI
Inserted data for hotel: HOTEL deMANCHI
Stored data for hotel: HOTEL deMANCHI
Address: •
Price: Rs 19,934
Total Reviews: 2,148 reviews
Average Review: 4.1
About: Off the N15 road, this relaxed budget hotel featuring mountain views is 9 km from Lake Saiful Muluk and 13 km from hiking at Lalazar Waterfall.… MoreCasual rooms, some with exposed beams, offer free Wi-Fi and flat-screen TVs; some have balconies. Rooms service is available 24/7.Amenities include 3 restaurants, a cafe, and a garden with views of the mountains. Parking is available.Check-in time: 14:00Check-out time: 12:00
Facilities: ParkingfreeBreakfastfreeWi-FifreeAir conditioning, InternetWi-FifreeServicesFront desk24-hourFull-service laundryPoolsNo poolsNo hot tubWellnessNo fitness centreNo spaFood and drinkRestaurantRoom serviceBreakfastfreeChildrenChild-friendlyParking & transportParkingfreeTransferLocal shuttleRoomsAir conditioning
Images: //lh5.googleusercontent.com/proxy/0bZUvES_-BBoLGN_RCj6IyPxUG2

Name: Frontier Hotel
Price element not found.
Hotel Frontier Hotel already exists in the database. Skipping insertion.
Stored data for hotel: Frontier Hotel
Address: WM58+5GC, Gheel Road, Katha, Naran, Mansehra, Khyber Pakhtunkhwa 21200
Price: N/A
Total Reviews: 4.7 (3,163)Picturesque lake known for views of rugged, sloping mountains & clear blue water.

 43 mins
Average Review: CloseView list
About: Check-out time: 12:00
Facilities: 
Images: //lh5.googleusercontent.com/proxy/BqncoxwGlDc9C3_ijE5JvlAsKunrEn5Rrv0RAvL2xz6fvijF1byEg3ZmBolcKE7AFpi6vUBwZJMuyRKJiSuCi3MbODoUF4vGmtk41Beeko0zfH5LqcPwX8sXHUGRkzTQJVopEVIy2GfWZBtnHCmpaB-0ppU1ZQ=w252-h186-k-no, //lh6.googleusercontent.com/proxy/f1IQ5FIuHtUqPXik92ymumBW8pyfU8AKeg5LjqouY4NNzUxaymkgfk7azX6rtN_IlzeNHykMNF6yGF33zTnxzfU9I1lqgb5X6UNCGWxB4RQ8cxjaxxJS8A1wIr_NOzLmZaekg3dV78zV5RYwvOGZlhD4g5cYiQ=w252-h156-k-no, //lh3.googleusercontent.com/proxy/9SYb4mggguNryYby4cOBWjQyJGJOk63kWn4nrtYK8cCXvKm1M1N3mAwcIHaYgFoC91RKwRY1hNOwoCjCGwlSxaGewRodS3UjgE2Nb

Name: Trout Lodges - King Room
address not avalible
Price element not found.
Inserted data for hotel: Trout Lodges - King Room
Stored data for hotel: Trout Lodges - King Room
Address: no address
Price: N/A
Total Reviews: Exact location provided after booking
Average Review: CloseView list
About: DetailsSituated in Ghumla, Trout Lodges features free WiFi, and guests can enjoy a garden, a terrace and a restaurant. The nearest airport is Gilgit Airport, 232 km from the lodge. The unit offers 1 bed.Website
Facilities: Entire house, Sleeps 2, 1 bedroom, 1 bathroom, 1 bed, Child-friendly, Pet-friendly, Free parking, Free Wi-Fi
Images: https://lh3.googleusercontent.com/proxy/Lb32b49cMQR_i1fbsYcVKF1I72HG0jdMSzaC7GoZ3NL59rv_nvgJr-mPu9BDEm4bcg4mdXUUJuCkLiI7ZvBxKcQ1bgpeyTI6tduSm5O0OWqupmgP2RS9MYpNyESd0rmwBKFc9XGtDx011gHvdjRI2TH8pYgw4g=s287-w287-h192-n-k-no-v1, https://lh3.googleusercontent.com/proxy/V-muPZZYYUrFFpClR-4DVHkoiSbnF2n4eUR6fPpaBRK48btgIptEq3CJ9TyzLe-9MGwhJztdtyUQg56fq0PMsE33GXkZTb7I2z